# 資料前處理

In [26]:
import json
file_path = 'dataset-1001-1125.json'
with open(file_path, 'r', encoding='utf-8') as file:
  analyze_data = json.load(file)

## 工具

In [27]:
len(analyze_data['articles'])

69103

In [28]:
import pandas as pd

def commentExtract(keyword_article_comment):
  all_article = []
  for kw in keywords_to_search:
    all_article += keyword_article_comment[kw]

  key_df = [pd.DataFrame(a) for a in all_article]
  commentDF = pd.concat(key_df, ignore_index=True)
  # print(commentDF)
  return commentDF

# useridSearch('DimlyLit', commentDF)

In [29]:
def comment(max_articles, keywords_to_search, data):
  # 要读取的前 100 个 article_title
  # max_articles = 69103

  # 计数器，用于记录已经读取的文章数量
  article_count = 0

  # 保存前 100 个 article_title
  article_titles = []
  article_ids = []

  # 用于记录已经遇到的关键字及其对应的文章标题
  keyword_dict = {}
  title_ids = {}

  # 關鍵字留言搜尋
  #keywords_to_search = ['陳其邁', '蘇貞昌', '俄羅斯', '柯文哲']  # 在这里替换为你要查找的关键字
  #for keyword in keywords_to_search:
  #    keyword_dict[keyword] = "初始"

  # 打开 JSON 文件



  # 從data(dict) 取出 articles(list)
  articles = data.get('articles', [])
  # print(f"文章內部可用資料：{articles[0].keys()}")
  # print(articles[0]['messages'][0].keys())
  user_ids = set()

  messageMerge(articles[2]['messages'])

  keyword_article_comment = dict()
  for keyword in keywords_to_search:
    keyword_article_comment[keyword] = list()

  # 迭代 articles 列表

  for article in articles:
      # 提取 article_title
      article_title = article.get('article_title')
      article_id = article.get('article_id')
      author = article.get('author')
      messages = article.get('messages')

      for i in range(len(keywords_to_search)):
        if keywords_to_search[i] in article_title:
          keyword_article, msg_count = messageMerge(messages)
          if (keyword_article == None) & (msg_count == None):
            continue
          keyword_article['article_title'] = [article_title for k in range(msg_count)]
          keyword_article['keyword'] = [keywords_to_search[i] for k in range(msg_count)]
          keyword_article['author'] = [author for k in range(msg_count)]
          # print(f"length of the messages: {msg_count}")
          keyword_article_comment[keywords_to_search[i]].append(keyword_article)


      # 如果 article_title 存在
      if article_title:
          # 将 article_title 添加到列表中
          article_titles.append(article_title)

          # 查找 article_title 中的关键字
          for keyword in keywords_to_search:
              if keyword in article_title:
                  # 如果关键字已经存在于字典中，则将文章标题添加到对应的列表中
                  if keyword in keyword_dict:
                      keyword_dict[keyword].append(article_title)
                      if article_title in title_ids:
                          title_ids[article_title].append(article_id)
                      else:
                          title_ids[article_title] = [article_id]
                  # 否则，创建新的列表并添加文章标题
                  else:
                      keyword_dict[keyword] = [article_title]


          # 打印文章标题
          #print(article_title)
          # 更新计数器
          article_count += 1

          # 如果已读取了前 max_articles 个 article_title，则停止
          if article_count >= max_articles:
              break

  #print("所有留言的使用者ID:")
  #for user_id in user_ids:
  #    print(user_id)
  # print() #排版
  # print("total users: ",len(user_ids))
  # print()

  # 打印关键字及其对应的文章标题
  # for keyword, titles in keyword_dict.items():
  #     print(f"Keyword: {keyword}")
  #     print("total articles ", len(titles))
  #     print("Titles:")
  #     for title in titles:
  #         print(f" - {title}")
  #         #print(title_ids[title])
  #     print()  # 换行以便于阅读
  return commentExtract(keyword_article_comment), articles


#### 合併5分鐘內的留言
- List of Dictionary 進入
- List Items 都是一則又一則的留言
-

- 遍歷單篇文章中的所有留言
  - timestamp =
  - 當前留言的id == 前一則留言的id：
    - 兩則留言時間相同：
      - timestamp 不變
      - 合併
    - timestamp += 1
      - 合併留言
  - 否：
    -

In [30]:
from datetime import datetime

def messageMerge(message):
  if len(message) == 0:
    return None, None
  first_comment = message[0]['push_ipdatetime'].split()
  time = []
  userid = []
  msg_content = []
  push = []
  # 初始化合併參數
  prev_id = message[0]['push_userid']                                            # 使用者ID UserID
                                                    # 日

  if len(first_comment) == 2: ## 如果留言沒有ID的話
    prev_date = first_comment[0]
    prev_time = (prev_date, int(first_comment[1][:2]), int(first_comment[1][-2:]))
    first_time = prev_time[2]
  else:
    prev_date = first_comment[1]
    prev_time = (prev_date, int(first_comment[2][:2]), int(first_comment[2][-2:])) # 日 時 分
    first_time = prev_time[2]
  timestamp = 0
  timeLimit = 5                                                                  # 時間限制
  push_tag = 0                                                                   # 用以記錄Push的值
  comment_count = 0
  prev_msg_content = ""
  msg_content = []
  transform = {'推': 0, '→':1, '噓':-1}
  #
  End_append = False

  # mergetime = msg['push_ipdatetime'][-5:]
  for msg in message:

    time_single_list = msg['push_ipdatetime'].split()
    # 留言區為空: Case
    if len(time_single_list) == 0:
      continue
    # 留言區沒有 ID: Case
    if len(time_single_list) == 2:
      # 時間資料有缺失的留言，直接刪除
      if len(time_single_list[1])!= 5:
        continue
      t = (time_single_list[0], int(time_single_list[1][:2]), int(time_single_list[1][-2:]))
    # 留言區正常：ID, 日期, 時間
    else:
      # 時間資料有缺失的留言，直接刪除
      if len(time_single_list[2])!= 5:
        continue
      if ((':' in time_single_list[2][:2]) or ':'in time_single_list[2][-2:]):
        pass
        # print(time_single_list)
        # print(time_single_list[2][:2],time_single_list[2][-2:])
      t = (time_single_list[1], int(time_single_list[2][:2]), int(time_single_list[2][-2:]))

    # 留言id
    id = msg['push_userid']
    # 前者留言 id 與當前 id 一樣
    if prev_id == id:
      # 留言時間差小於
      # timeLimit - timestamp = 容納留言時間寬度
      # mergetime[0] == t[0] 同天留言
      # timestamp
      if (t[2] - prev_time[2] < timeLimit - timestamp) & (prev_time[0] == t[0]) & (timestamp < timeLimit):
        push_tag += transform[msg['push_tag']] # 轉成數值
        comment_count += 1 # 計算Comment Count
        timestamp = t[2] - prev_time[2]
        if t[2] != first_time:
          prev_msg_content += ("/" + msg['push_content'])
      else:
        comment_count += 1
        push_tag += transform[msg['push_tag']]
        push.append(push_tag/comment_count)
        timestamp = 0
        msg_content.append(prev_msg_content)
        userid.append(prev_id)
        time.append(prev_time)
        comment_count = 0
        push_tag = 0
        prev_id = id
        prev_time = t
        prev_msg_content = msg['push_content']
    # 前個留言的人與此次留言的人不同 Case
    else :
      comment_count += 1
      # Updating Features
      push_tag += transform[msg['push_tag']]
      # Storing Features
      push.append(push_tag/comment_count)
      End_append = True
      msg_content.append(prev_msg_content)
      userid.append(prev_id)
      time.append(prev_time)
      # Initialization
      comment_count = 0
      push_tag = 0
      prev_id = id
      prev_time = t
      prev_msg_content = msg['push_content']
  if End_append:
    comment_count += 1
    push_tag += transform[msg['push_tag']]
    push.append(push_tag/comment_count)
    userid.append(prev_id)
    time.append(prev_time)
    msg_content.append(prev_msg_content)
  return {'userid':userid, "time":time, "message_content":msg_content, "push_tag":push}, len(userid)


  # print()
  # print("Before Merge")
  # print(f"Message Count: {len(message)}")
  # print()
  # for i in range(len(message)):
  #   time_single_list = message[i]['push_ipdatetime'].split()
  #   t = (time_single_list[1], int(time_single_list[2][:2]), int(time_single_list[2][-2:]))
  #   print(f"UserID: {message[i]['push_userid']}, MessageTime: {t}, MessageContent: {message[i]['push_content']}")

  # print()
  # print("After Merge")
  # print(f"Message Count: {len(userid)}")
  # print()
  # for i in range(len(userid)):
  #   print(f"UserID: {userid[i]}, MessageTime: {time[i]}, MessageContent: {msg_content[i]}")


#### 特定使用者搜尋


In [31]:
def useridSearch (userid, df):
  # 使用布林索引找到 "City" 列中包含 "New York" 的所有行
  filtered_df = df[df['userid'] == userid]

  # 打印結果
  # print(filtered_df)
  return filtered_df

#### 汲取 Repost 文章

In [32]:
def todate(str_lst):
  date = None
  map = {'Oct':'10', 'Nov':'11', 'Dec':'12'}
  if len(str_lst[2]) == 1:
    date = map[str_lst[1]]+'/' + '0' +str_lst[2]
  else:
    date = map[str_lst[1]]+'/' + str_lst[2]
  h_m = str_lst[3].split(':')
  return '(' + date + ', ' + h_m[0] + ', '+ h_m[1] + ')'

def repostExtract(articles):
  userid = []
  time = []
  msg_content = []
  push = []
  keyword = []
  article_title = []
  count = 0
  for post in articles:
    for i in range(len(keywords_to_search)):
      if (post['article_title'][:3] == 'Re:' )& (keywords_to_search[i] in post['article_title']):
        userid.append(post['author'])
        msg_content.append(post['content'])
        time.append(todate(post['date'].split()))
        keyword.append(keywords_to_search[i])
        article_title.append(post['article_title'])

  push = [2 for i in range(len(msg_content))]
  return len(userid), pd.DataFrame({'userid':userid, "time":time, "message_content":msg_content, "push_tag":push, "article_title": article_title, "keyword": keyword, "author": userid})

# rp_count, repostDF = repostExtract(articles)
# print(f'Total Number of Reposted Articles :{rp_count}')

合併

## 資料準備

In [33]:
# 文章數量太多可以減少，最多就是 69103 篇
# keywords 可以更改
max_articles = 69103
#keywords_to_search = ['黃國昌', '柯文哲', '蘇貞昌', '侯友宜']
keywords_to_search = ['黃國昌']

# 這邊不用管
commentDF, articles = comment(max_articles, keywords_to_search, analyze_data)
rp_count, repostDF = repostExtract(articles)

final = pd.concat([commentDF, repostDF], ignore_index= True)
final["push_tag"] = final["push_tag"].apply(lambda x: 0 if x == 2 else (1 if x > 0 else (-1 if x < 0 else 0)))

# 輸出成excel檔
# final.to_excel("留言.xlsx")

# 1. 呼叫整個dataframe觀察
#final

# 2. 只看特定user的使用習慣：useridSearch 可以透過更改 userid 直接搜尋其留言
#user = useridSearch('prkfcpr',final)
#print(f"共有:{len(user)}則")
#user

# 3. 針對特定用戶輸出他的所有留言，成excel檔
# useridSearch('prkfcpr',final).to_excel

from collections import Counter
userid_counts = Counter(final['userid'])

# 找出出現次數最高的三個userid
top_3_userids = userid_counts.most_common(3)

# 建立結果字典
result_dict = {userid: count for userid, count in top_3_userids}
#print(result_dict)
#黃國昌的
#user = useridSearch('akirakid',final)
#user = useridSearch('stvn2567',final)
#user = useridSearch('lmf770410',final)
#print(f"共有:{len(user)}則")
final

userid             time  \
0                             bybe  (10/01, 11, 46)   
1                           spzper  (10/01, 11, 46)   
2                         tchialen  (10/01, 11, 46)   
3                      IamHsihPing  (10/01, 11, 46)   
4                          a210510  (10/01, 11, 46)   
...                            ...              ...   
8831               ice80712 (打臉腦粉)  (11/21, 09, 33)   
8832              sunyeah (   湯元嗎)  (11/21, 17, 32)   
8833  chopper594 (世界のももクロ No.1!!!)  (11/21, 17, 34)   
8834               slamguyno1 (布魯)  (11/21, 18, 11)   
8835                    A6 (短ID真好)  (11/21, 18, 31)   

                                        message_content  push_tag  \
0                                                               1   
1                                            抓到國昌挺中共同路3         0   
2                                           中共同路人挺中共同路人         0   
3                                               柯韓昌粉一家親         0   
4                                               抓到國師挺柯p         0   
...                                                 ...       ...   
8831  所以黃國昌有當兵嗎? 時代力量支持者常常說民進黨抗中保台是假的，騙票是真的， 時代力量才是真...         0   
8832  加入33團隊的話 那如果黃珊珊當選台北市長的話 黃國昌可以接任法務局長吧 副市長應該不太適合...         0   
8833  : 新頭殼 : 邱于真 : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情...         0   
8834  : 加入33團隊的話 : 那如果黃珊珊當選台北市長的話 : 黃國昌可以接任法務局長吧 : 副...         0   
8835  : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情 : 九合一選戰進入倒數...         0   

                      article_title keyword                        author  
0     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)  
1     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)  
2     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)  
3     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)  
4     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)  
...                             ...     ...                           ...  
8831  Re: [新聞] 現身挺黃珊珊！黃國昌：抗中保台是全民DN     黃國昌               ice80712 (打臉腦粉)  
8832   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌              sunyeah (   湯元嗎)  
8833   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌  chopper594 (世界のももクロ No.1!!!)  
8834   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌               slamguyno1 (布魯)  
8835   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌                    A6 (短ID真好)  

[8836 rows x 7 columns]

# 模型

## 庭徹模型1

In [34]:
import pandas as pd
import jieba
from keras import preprocessing
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import matplotlib.pyplot as plt
import numpy as np
import glob

# Get CSV files list from a folder
path = './data/datasets'
csv_files = glob.glob(path + "/*.csv")

# Read each CSV file into DataFrame
# This creates a list of dataframes
df_list = (pd.read_csv(file) for file in csv_files)

# Concatenate all DataFrames
raw_data = pd.concat(df_list, ignore_index=True)
#print(raw_data)
print(raw_data['label'].value_counts())

label
0    10431
1     9322
Name: count, dtype: int64


In [35]:
from sklearn.utils import resample

# 分離每個類別的數據
df_majority = raw_data[raw_data['label'] == 1]
df_minority = raw_data[raw_data['label'] == 0]

# 上採樣少數類別
df_minority_upsampled = resample(df_minority, 
                                 replace=True,     # 允许放回抽样
                                 n_samples=len(df_majority),    # 与多数类数量一致
                                 random_state=123) # 固定随机种子

# 合併多數類別和上採樣後的少數類別
data = pd.concat([df_majority, df_minority_upsampled])

# 打亂數據
data = data.sample(frac=1, random_state=123).reset_index(drop=True)

# 檢查數據平衡狀況
print(data['label'].value_counts())
#print(data)

data['sentence'] = data['sentence'].astype(str)

# 斷詞
data['cut_sentence'] = data['sentence'].apply(lambda x: ' '.join(jieba.cut(x)))
# m = data.shape[0]
# print(data.loc[0, 'sentence'])
# sentence_words = jieba.lcut(data.loc[0, 'sentence'], cut_all=False, HMM=True)
# print(sentence_words)
# for i in range(m):
#     sentence_words = jieba.lcut(data.loc[i, 'sentence'], cut_all=False, HMM=True)

# 使用Tokenizer將詞轉換為數字
tokenizer = Tokenizer()
tokenizer.fit_on_texts(data['cut_sentence'])
sequences = tokenizer.texts_to_sequences(data['cut_sentence'])

# 填充序列，使得每個序列長度相同
max_sequence_length = 100
data_matrix = pad_sequences(sequences, maxlen=max_sequence_length)

# 獲取標籤
labels = data['label'].values

label
0    9322
1    9322
Name: count, dtype: int64


In [36]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset

# 定義Dataset類
class SentimentDataset(Dataset):
    def __init__(self, data_matrix, labels):
        self.data_matrix = data_matrix
        self.labels = labels

    def __len__(self):
        return len(self.data_matrix)

    def __getitem__(self, idx):
        return torch.tensor(self.data_matrix[idx], dtype=torch.long), torch.tensor(self.labels[idx], dtype=torch.float)

# 創建Dataset和DataLoader
dataset = SentimentDataset(data_matrix, labels)
train_size = int(0.8 * len(dataset))
test_size = len(dataset) - train_size
train_dataset, test_dataset = torch.utils.data.random_split(dataset, [train_size, test_size])

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

# 定義LSTM模型
class SentimentLSTM(nn.Module):
    def __init__(self, vocab_size, embedding_dim, hidden_dim, output_dim):
        super(SentimentLSTM, self).__init__()
        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, batch_first=True)
        self.fc = nn.Linear(hidden_dim, output_dim)
        self.sigmoid = nn.Sigmoid()

    def forward(self, x):
        embedded = self.embedding(x)
        lstm_out, _ = self.lstm(embedded)
        lstm_out = lstm_out[:, -1, :]  # 取最後一個timestep的輸出
        out = self.fc(lstm_out)
        return self.sigmoid(out)

# 模型参數
embedding_dim = 100  # 嵌入層維度
hidden_dim = 128
output_dim = 1
vocab_size = len(tokenizer.word_index) + 1

# 初始化模型、損失函數和optimizer
model = SentimentLSTM(vocab_size, embedding_dim, hidden_dim, output_dim)
criterion = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

#epoch
num_epochs = 10

train_losses, test_losses, accuracies = [], [], []

for epoch in range(num_epochs):
    model.train()
    total_train_loss = 0
    for inputs, targets in train_loader:
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs.squeeze(), targets)
        loss.backward()
        optimizer.step()
        total_train_loss += loss.item()
    
    avg_train_loss = total_train_loss / len(train_loader)
    
    model.eval()
    total_test_loss = 0
    correct = 0
    total = 0

    with torch.no_grad():
        for inputs, targets in test_loader:
            outputs = model(inputs)
            loss = criterion(outputs.squeeze(), targets)
            total_test_loss += loss.item()
            predicted = (outputs.squeeze() > 0.5).float()
            total += targets.size(0)
            correct += (predicted == targets).sum().item()

    avg_test_loss = total_test_loss / len(test_loader)
    accuracy = correct / total

    train_losses.append(avg_train_loss)
    test_losses.append(avg_test_loss)
    accuracies.append(accuracy)

    print(f'Epoch {epoch+1}/{num_epochs}, Train Loss: {avg_train_loss:.4f}, Test Loss: {avg_test_loss:.4f}, Accuracy: {accuracy:.4f}')

model.eval()
correct = 0
total = 0

with torch.no_grad():
    for inputs, targets in test_loader:
        outputs = model(inputs)
        predicted = (outputs.squeeze() > 0.5).float()
        total += targets.size(0)
        correct += (predicted == targets).sum().item()

accuracy = correct / total
print(f'Test Accuracy: {accuracy:.2f}')

Epoch 1/10, Train Loss: 0.4739, Test Loss: 0.4157, Accuracy: 0.8174
Epoch 2/10, Train Loss: 0.3306, Test Loss: 0.3508, Accuracy: 0.8530
Epoch 3/10, Train Loss: 0.2596, Test Loss: 0.3116, Accuracy: 0.8791
Epoch 4/10, Train Loss: 0.1861, Test Loss: 0.3101, Accuracy: 0.8898
Epoch 5/10, Train Loss: 0.1386, Test Loss: 0.3484, Accuracy: 0.8871
Epoch 6/10, Train Loss: 0.0980, Test Loss: 0.3383, Accuracy: 0.8914
Epoch 7/10, Train Loss: 0.0675, Test Loss: 0.3698, Accuracy: 0.8793
Epoch 8/10, Train Loss: 0.0544, Test Loss: 0.3793, Accuracy: 0.8976
Epoch 9/10, Train Loss: 0.0463, Test Loss: 0.4489, Accuracy: 0.8957
Epoch 10/10, Train Loss: 0.0247, Test Loss: 0.4350, Accuracy: 0.9037
Test Accuracy: 0.90


## TC1

In [37]:
def predict_sentiment_TC1(sentence, model, tokenizer, max_sequence_length):
    model.eval()
    sentence = ' '.join(jieba.lcut(sentence, cut_all=False, HMM=True))
    sequence = tokenizer.texts_to_sequences([sentence])
    padded_sequence = pad_sequences(sequence, maxlen=max_sequence_length)
    input_tensor = torch.tensor(padded_sequence, dtype=torch.long)
    with torch.no_grad():
        output = model(input_tensor)
    # Positive if > 0.5, 0 if 0
    #sentiment = lambda x: 0 if output.item()==0 else(1 if output.item() > 0.5 else -1)
    sentiment = 1 if output.item() > 0.5 else -1
    #sentiment = 'Positive' if output.item() > 0.5 else 'Negative'
    return sentiment

In [38]:
eomtions_model_TC_1 = []
for i in final["message_content"]:
    test_sentence = i
    emotion_TC1 = predict_sentiment_TC1(test_sentence, model, tokenizer, max_sequence_length) 
    eomtions_model_TC_1.append(emotion_TC1)
    #print(f"Sentence: '{test_sentence}' -> Sentiment: {predict_sentiment(test_sentence, model, tokenizer, max_sequence_length)}")
#eomtions_model_TC_1


In [79]:
final_with_TC1 = final.copy()
final_with_TC1["LSTM_emotions"] = eomtions_model_TC_1
final_with_TC1

userid             time  \
0                             bybe  (10/01, 11, 46)   
1                           spzper  (10/01, 11, 46)   
2                         tchialen  (10/01, 11, 46)   
3                      IamHsihPing  (10/01, 11, 46)   
4                          a210510  (10/01, 11, 46)   
...                            ...              ...   
8831               ice80712 (打臉腦粉)  (11/21, 09, 33)   
8832              sunyeah (   湯元嗎)  (11/21, 17, 32)   
8833  chopper594 (世界のももクロ No.1!!!)  (11/21, 17, 34)   
8834               slamguyno1 (布魯)  (11/21, 18, 11)   
8835                    A6 (短ID真好)  (11/21, 18, 31)   

                                        message_content  push_tag  \
0                                                               1   
1                                            抓到國昌挺中共同路3         0   
2                                           中共同路人挺中共同路人         0   
3                                               柯韓昌粉一家親         0   
4                                               抓到國師挺柯p         0   
...                                                 ...       ...   
8831  所以黃國昌有當兵嗎? 時代力量支持者常常說民進黨抗中保台是假的，騙票是真的， 時代力量才是真...         0   
8832  加入33團隊的話 那如果黃珊珊當選台北市長的話 黃國昌可以接任法務局長吧 副市長應該不太適合...         0   
8833  : 新頭殼 : 邱于真 : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情...         0   
8834  : 加入33團隊的話 : 那如果黃珊珊當選台北市長的話 : 黃國昌可以接任法務局長吧 : 副...         0   
8835  : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情 : 九合一選戰進入倒數...         0   

                      article_title keyword                        author  \
0     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
1     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
2     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
3     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
4     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
...                             ...     ...                           ...   
8831  Re: [新聞] 現身挺黃珊珊！黃國昌：抗中保台是全民DN     黃國昌               ice80712 (打臉腦粉)   
8832   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌              sunyeah (   湯元嗎)   
8833   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌  chopper594 (世界のももクロ No.1!!!)   
8834   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌               slamguyno1 (布魯)   
8835   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌                    A6 (短ID真好)   

      LSTM_emotions  
0                 1  
1                 1  
2                -1  
3                -1  
4                 1  
...             ...  
8831              1  
8832             -1  
8833             -1  
8834              1  
8835             -1  

[8836 rows x 8 columns]

## 庭徹模型2

In [40]:
# 讀取資料集
ntusd_df = pd.read_csv('./data/ntusd-full.csv')

# 檢查資料
print(ntusd_df.head())

from sklearn.feature_extraction.text import TfidfVectorizer

# 將詞語轉換成特徵向量
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(ntusd_df['word'])
y = ntusd_df['sentiment']

        word sentiment
0          幹        負面
1      一下子爆發        負面
2  一下子爆發的一連串        負面
3        一巴掌        負面
4         一再        負面


In [41]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, accuracy_score

# 分割資料集為訓練集和測試集
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 訓練Random Forest模型
rf_classifier = RandomForestClassifier(n_estimators=100, random_state=42)
rf_classifier.fit(X_train, y_train)

# 預測
y_pred = rf_classifier.predict(X_test)

# 評估模型
print("Accuracy:", accuracy_score(y_test, y_pred))
print("Classification Report:\n", classification_report(y_test, y_pred))

Accuracy: 0.7600360847992783
Classification Report:
               precision    recall  f1-score   support

          正面       0.94      0.08      0.14       574
          負面       0.76      1.00      0.86      1643

    accuracy                           0.76      2217
   macro avg       0.85      0.54      0.50      2217
weighted avg       0.80      0.76      0.68      2217



In [42]:
import jieba

emotions_model_TC_2 = []

def predict_sentiment_TC2(sentence):
    # 分詞
    words = jieba.lcut(sentence)
    #print(words)
    # 過濾不在詞典中的詞
    filtered_words = [word for word in words if word in vectorizer.vocabulary_]
    # 如果沒有情緒詞彙，返回中立
    if not filtered_words:
        emotions_model_TC_2.append(0)
        return 'neutral'
    # 將過濾後的詞語轉換為特徵向量
    text_vector = vectorizer.transform([' '.join(filtered_words)])
    # 預測情緒
    sentiment = rf_classifier.predict(text_vector)
    emotion = 1 if sentiment == '正面' else -1
    emotions_model_TC_2.append(emotion)
    #print(sentiment.size)
    #return sentiment[0][0]



# 測試新句子
#print(predict_sentiment_TC2('我今天很快樂'))  # 測試正面情緒
#print(predict_sentiment_TC2('這是一個糟糕的日子'))  # 測試負面情緒



## TC2

In [43]:
emotions_model_TC_2 = []
for i in final["message_content"]:
    test_sentence = i
    if len(test_sentence) == 0:
        emotions_model_TC_2.append('0')
    else:
        predict_sentiment_TC2(test_sentence)
    #print(predict_sentiment_TC2(test_sentence))
    #emotion = lambda x: 0 if predict_sentiment_TC2(test_sentence) == 'neutral' else(1 if predict_sentiment_TC2(test_sentence) == "正面" else -1)
    #print(emotion)
    #emotions_model_TC_2.append(emotion)
#emotions_model_TC_2

['抓到', '國昌', '挺', '中', '共同', '路', '3']
['中共', '同路人', '挺', '中共', '同路人']
['柯韓昌粉', '一家', '親']
['抓到', '國師', '挺', '柯', 'p']
['推戰神']
['都', '是', '中共', '同路人', '不', '1', '歪']
['棄', '中保', '3', '？']
['讚', '喔']
['昌黑', '表示', '有點', '意外']
['阿中粉', '：', '抓到', '了', '！', '森', '77', '！']
['支持', '第三', '勢力', ' ', '珊珊']
['戰神', '當初', '應該', '繼續當', '立委', '的', ' ', ' ', '可惜']
['33', '加油', '~']
['當初', '應該', '繼續', '選', '立委', '的', ' ', '可惜', ' ', '這次', '為', '了', '挺']
['沒錯']
['中', '共同', '路', '三']
['他', '可以', '當阿', ' ', '不分區', '上面', '自己', '辭掉', '就', '好']
['陳', '宥', '丞要', '被棄', '了', '嗎', '？']
['子弟兵', ' ', '連', '33', '都', '要', '蹭', '了', ' ', '畢竟', '每次', '子弟兵', '都']
['那個', '她', '的', '子弟兵', ' ', '是不是', '沒機會', '上', '了', '？']
['是', '要', '叫', '邱顯', '智辭', '掉', '嗎']
['反正', '時代', '的', '票', '也', '都', '國昌', '掙來', '的']
['沒選上', '很慘']
['國濕', '總算', '清醒', '了', ' ', '繼續', '挺民進', '党', '沒', '好', '處']
['陳', '宥', '丞', '沒', '有', '被棄', ' ', ' ', '都', '不', '看', '內文', '的', '嗎', '=', ' ', '=']
['來', ' ', '阿昌', ' ', '自己', '去', '挑', '一根', '路燈']


In [80]:
final_with_TC2 = final.copy()
final_with_TC2["RF_emotions"] = emotions_model_TC_2
final_with_TC2

userid             time  \
0                             bybe  (10/01, 11, 46)   
1                           spzper  (10/01, 11, 46)   
2                         tchialen  (10/01, 11, 46)   
3                      IamHsihPing  (10/01, 11, 46)   
4                          a210510  (10/01, 11, 46)   
...                            ...              ...   
8831               ice80712 (打臉腦粉)  (11/21, 09, 33)   
8832              sunyeah (   湯元嗎)  (11/21, 17, 32)   
8833  chopper594 (世界のももクロ No.1!!!)  (11/21, 17, 34)   
8834               slamguyno1 (布魯)  (11/21, 18, 11)   
8835                    A6 (短ID真好)  (11/21, 18, 31)   

                                        message_content  push_tag  \
0                                                               1   
1                                            抓到國昌挺中共同路3         0   
2                                           中共同路人挺中共同路人         0   
3                                               柯韓昌粉一家親         0   
4                                               抓到國師挺柯p         0   
...                                                 ...       ...   
8831  所以黃國昌有當兵嗎? 時代力量支持者常常說民進黨抗中保台是假的，騙票是真的， 時代力量才是真...         0   
8832  加入33團隊的話 那如果黃珊珊當選台北市長的話 黃國昌可以接任法務局長吧 副市長應該不太適合...         0   
8833  : 新頭殼 : 邱于真 : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情...         0   
8834  : 加入33團隊的話 : 那如果黃珊珊當選台北市長的話 : 黃國昌可以接任法務局長吧 : 副...         0   
8835  : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情 : 九合一選戰進入倒數...         0   

                      article_title keyword                        author  \
0     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
1     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
2     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
3     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
4     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
...                             ...     ...                           ...   
8831  Re: [新聞] 現身挺黃珊珊！黃國昌：抗中保台是全民DN     黃國昌               ice80712 (打臉腦粉)   
8832   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌              sunyeah (   湯元嗎)   
8833   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌  chopper594 (世界のももクロ No.1!!!)   
8834   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌               slamguyno1 (布魯)   
8835   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌                    A6 (短ID真好)   

     RF_emotions  
0              0  
1              0  
2              0  
3              0  
4              0  
...          ...  
8831        -1.0  
8832        -1.0  
8833        -1.0  
8834        -1.0  
8835        -1.0  

[8836 rows x 8 columns]

## 品皙模型

In [54]:
import pandas as pd
import jieba
from keras import preprocessing
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
import matplotlib.pyplot as plt
import numpy as np
import glob

# 從資料夾取得csv檔清單
path = './newdataset'
csv_files = glob.glob(path + "/*.csv")

# 將所有csv檔讀進dataframes
# 建立dataframes的清單
df_list = (pd.read_csv(file) for file in csv_files)

# 組合所有dataframes
raw_data = pd.concat(df_list, ignore_index=True)
print(raw_data)
print(raw_data['label'].value_counts())

       label                                           sentence  cat review
0          1  距离川沙公路较近,但是公交指示不对,如果是"蔡陆线"的话,会非常麻烦.建议用别的路线.房间较...  NaN    NaN
1          1                       商务大床房，房间很大，床有2M宽，整体感觉经济实惠不错!  NaN    NaN
2          1         早餐太差，无论去多少人，那边也不加食品的。酒店应该重视一下这个问题了。房间本身很好。  NaN    NaN
3          1  宾馆在小街道上，不大好找，但还好北京热心同胞很多~宾馆设施跟介绍的差不多，房间很小，确实挺小...  NaN    NaN
4          1               CBD中心,周围没什么店铺,说5星有点勉强.不知道为什么卫生间没有电吹风  NaN    NaN
...      ...                                                ...  ...    ...
82522      0                                 以前几乎天天吃，现在调料什么都不放，  NaN    NaN
82523      0           昨天订凉皮两份，什么调料都没有放，就放了点麻油，特别难吃，丢了一份，再也不想吃了  NaN    NaN
82524      0                                          凉皮太辣,吃不下都  NaN    NaN
82525      0                                       本来迟到了还自己点！！！  NaN    NaN
82526      0                  肉夹馍不错，羊肉泡馍酱肉包很一般。凉面没想象中好吃。送餐倒是很快。  NaN    NaN

[82527 rows x 4 columns]
label
0    41477
1    41050
Name: count, dtype: int64


In [55]:
from sklearn.utils import resample

# 分離每個類別的數據
df_majority = raw_data[raw_data['label'] == 1]
df_minority = raw_data[raw_data['label'] == 0]

# 上採樣少數類別
df_minority_upsampled = resample(df_minority, 
                                 replace=True,     # 允许放回抽样
                                 n_samples=len(df_majority),    # 与多数类数量一致
                                 random_state=123) # 固定随机种子

# 合併多數類別和上採樣後的少數類別
data = pd.concat([df_majority, df_minority_upsampled])

# 打亂數據
data = data.sample(frac=1, random_state=123).reset_index(drop=True)

# 檢查數據平衡狀況
print(data['label'].value_counts())
print(data)

label
0    41050
1    41050
Name: count, dtype: int64
       label sentence  cat                                             review
0          0      NaN  洗发水  刚买就降价、申请退款没成功、本来想拒收、快递来了电话都不打就给我放单位了、申请价格保护还给我...
1          0      NaN  洗发水     买的慎选，我一次买了两瓶，洗了头发一点也不顺，像一团乱麻，梳都梳不开，这样的价格我只能呵呵了
2          0      NaN   酒店                     无窗，住落后感觉压抑，特别到早上了，还不知道外面情况，不好。
3          0   永远不看备注  NaN                                                NaN
4          1      NaN  洗发水                   大品牌，家里一直用清扬！这次套装很划算，还送了两瓶试用装，不错！
...      ...      ...  ...                                                ...
82095      0      NaN   酒店             服务态度不好，极差，前台态度恶劣，房间卫生不干净，诬陷客人照成，要求客人赔偿
82096      0      NaN   水果     给的是最小的吗？买第一次时大小还行，这次买的还没梨大，今天准备吃时，发现长毛了，不会再次购买
82097      1      NaN   水果                  水果很新鲜 物流也很快 家人很喜欢 还会继续购买 很甜 给家人买的
82098      1      NaN   衣服                                    修身，款型好，穿着舒适，喜欢！
82099      1      NaN   水果                                    好吃，汁多、脆、香甜，值得推荐

[82100 ro

### 把data存進 data set 
#### 建立train val test path

In [56]:
import pandas as pd
from sklearn.model_selection import train_test_split
import os
import jieba

total_data_path = './newdataset/total_data.txt'
train_data_path = './newdataset/train_data.txt'
val_data_path = './newdataset/validation_data.txt'
test_data_path = './newdataset/test_data.txt'

os.makedirs(os.path.dirname(train_data_path), exist_ok=True)
os.makedirs(os.path.dirname(val_data_path), exist_ok=True)
os.makedirs(os.path.dirname(test_data_path), exist_ok=True)

# 將data分詞後存入total_data.txt
jieba.case_sensitive = True
with open(total_data_path, 'w', encoding='utf-8', errors='replace') as total_data:
    for i, row in data.iterrows():
        line = ' '.join(map(str, row.values)).replace('\n', ' ')
        words = jieba.cut(line)
        line_new = ' '.join(words)
        total_data.write(line_new + '\n')

# 分成分成train, val, test data set
dataset_path = './newdataset/total_data.txt'
with open(dataset_path, 'r', encoding='utf-8') as file:
    data = file.readlines()

data = [line.strip() for line in data]
df = pd.DataFrame(data, columns=["text"])

train_data, temp_data = train_test_split(df, test_size=0.3, random_state=42)
val_data, test_data = train_test_split(temp_data, test_size=0.66, random_state=42)

train_data = train_data.reset_index(drop=True)
val_data = val_data.reset_index(drop=True)
test_data = test_data.reset_index(drop=True)

def save_to_txt(dataframe, file_path):
    with open(file_path, 'w', encoding='utf-8') as f:
        for text in dataframe['text']:
            f.write(text + '\n')

output_dir = './newdataset'
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

save_to_txt(train_data, os.path.join(output_dir, 'train.txt'))
save_to_txt(val_data, os.path.join(output_dir, 'val.txt'))
save_to_txt(test_data, os.path.join(output_dir, 'test.txt'))

print("成功保存")


成功保存


In [57]:
from __future__ import unicode_literals, print_function, division
import torch
import torch.nn as nn
import torch.nn.functional as F


class LSTMModel(nn.Module):
    def __init__(
        self,
        vocab_size,
        embedding_dim,
        pretrained_weight,
        update_w2v,
        hidden_dim,
        num_layers,
        drop_keep_prob,
        n_class,
        bidirectional,
        **kwargs
    ):
        """
        @description: initial seetings
        @param {*}
        - vocab_size: int, vocabulary size.
        - embedding_dim: int, the embedding layer dim.
        - pretrained_weight: Tensor, FloatTensor containing weights for the Embedding.
        - update_w2v: bool, whether to update word2vec embedding weight.
        - hidden_dim: int, the hidden layer dim.
        - num_layers: int, the number of layers.
        - drop_keep_prob: float, the keep probability of dropout layer.
        - n_class: int, the number of classes (labels).
        - bidirectional: bool, whether to use bidirectional LSTM.
        @return {*}
        None
        """
        super(LSTMModel, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers
        self.n_class = n_class

        self.bidirectional = bidirectional
        self.embedding = nn.Embedding.from_pretrained(pretrained_weight)
        self.embedding.weight.requires_grad = update_w2v
        self.encoder = nn.LSTM(
            input_size=embedding_dim,
            hidden_size=self.hidden_dim,
            num_layers=num_layers,
            bidirectional=self.bidirectional,
            dropout=drop_keep_prob,
        )

        if self.bidirectional:
            self.decoder1 = nn.Linear(hidden_dim * 4, hidden_dim)
            self.decoder2 = nn.Linear(hidden_dim, n_class)
        else:
            self.decoder1 = nn.Linear(hidden_dim * 2, hidden_dim)
            self.decoder2 = nn.Linear(hidden_dim, n_class)

    def forward(self, inputs):
        # inputs: (num_embeddings, embedding_dim) => [batch, seq_len, embed_dim]:[64,75,50]
        embeddings = self.embedding(inputs)
        # LSTM input:(seq, batch, input_size) => [seq_len, batch, embed_dim]:[75,64,50]
        states, hidden = self.encoder(embeddings.permute([1, 0, 2]))
        # states: (seq_len, batch, D*hidden_size), D=2 if bidirectional = True else 1, =>[75,64,256]
        # hidden: (h_n, c_n) => h_n / c_n shape:(D∗num_layers, batch, hidden_size) =>[4,64,128]
        encoding = torch.cat([states[0], states[-1]], dim=1)
        # encoding shape: (batch, 2*D*hidden_size): [64,512]
        outputs = self.decoder1(encoding)
        # outputs = F.softmax(outputs, dim=1)
        outputs = self.decoder2(outputs)  # outputs shape:(batch, n_class) => [64,2]
        return outputs


class LSTM_attention(nn.Module):
    def __init__(
        self,
        vocab_size,
        embedding_dim,
        pretrained_weight,
        update_w2v,
        hidden_dim,
        num_layers,
        drop_keep_prob,
        n_class,
        bidirectional,
        **kwargs
    ):
        """
        @description: initial seetings
        @param {*}
        - vocab_size: int, vocabulary size.
        - embedding_dim: int, the embedding layer dim.
        - pretrained_weight: Tensor, FloatTensor containing weights for the Embedding.
        - update_w2v: bool, whether to update word2vec embedding weight.
        - hidden_dim: int, the hidden layer dim.
        - num_layers: int, the number of layers.
        - drop_keep_prob: float, the keep probability of dropout layer.
        - n_class: int, the number of classes (labels).
        - bidirectional: bool, whether to use bidirectional LSTM.
        @return {*}
        None
        """
        super(LSTM_attention, self).__init__()
        self.hidden_dim = hidden_dim
        self.num_layers = num_layers
        self.n_class = n_class

        self.bidirectional = bidirectional
        self.embedding = nn.Embedding.from_pretrained(pretrained_weight)
        self.embedding.weight.requires_grad = update_w2v
        self.encoder = nn.LSTM(
            input_size=embedding_dim,
            hidden_size=self.hidden_dim,
            num_layers=num_layers,
            bidirectional=self.bidirectional,
            dropout=drop_keep_prob,
        )

        # What is nn. Parameter(data(Tensor)=None, requires_grad=True) ? Explain
        # 理解为类型转换函数，将一个不可训练的类型Tensor转换成可以训练的类型parameter.
        # 所以经过类型转换这个Tensor变成了模型的一部分，成为了模型中根据训练可以改动的参数了。
        # 使用这个函数的目的也是想让某些变量在学习的过程中不断的修改其值以达到最优化。
        self.weight_W = nn.Parameter(torch.Tensor(2 * hidden_dim, 2 * hidden_dim))
        self.weight_proj = nn.Parameter(torch.Tensor(2 * hidden_dim, 1))

        if self.bidirectional:
            self.decoder1 = nn.Linear(hidden_dim * 2, hidden_dim)
            self.decoder2 = nn.Linear(hidden_dim, n_class)
        else:
            self.decoder1 = nn.Linear(hidden_dim, hidden_dim)
            self.decoder2 = nn.Linear(hidden_dim, n_class)

        nn.init.uniform_(self.weight_W, -0.1, 0.1)
        nn.init.uniform_(self.weight_proj, -0.1, 0.1)

    def forward(self, inputs):
        embeddings = self.embedding(inputs)
        states, hidden = self.encoder(embeddings.permute([0, 1, 2]))
        # attention:
        u = torch.tanh(torch.matmul(states, self.weight_W))
        att = torch.matmul(u, self.weight_proj)
        att_score = F.softmax(att, dim=1)
        scored_x = states * att_score

        encoding = torch.sum(scored_x, dim=1)
        outputs = self.decoder1(encoding)
        outputs = self.decoder2(outputs)
        return outputs

#### 模型參數

In [61]:
class Config:
    update_w2v = True  # 是否在训练中更新w2v
    vocab_size = 54848  # 词汇量，与word2id中的词汇量一致
    n_class = 2  # 分类数：分别为pos和neg
    max_sen_len = 100  # 句子最大长度
    embedding_dim = 50  # 词向量维度
    batch_size = 64  # 批处理尺寸
    hidden_dim = 128  # 隐藏层节点数
    n_epoch = 5  # 训练迭代周期，即遍历整个训练样本的次数
    lr = 0.0001  # 学习率；若opt=‘adadelta'，则不需要定义学习率
    drop_keep_prob = 0.2  # dropout层，参数keep的比例
    num_layers = 2  # LSTM层数
    bidirectional = True  # 是否使用双向LSTM
    model_dir = "./model"
    stopword_path = './data/stopword.txt'
    train_path = './newdataset/train.txt'
    val_path = './newdataset/val.txt'
    test_path = './newdataset/test.txt'
    pre_path = "./data/pre.txt"
    word2id_path = "./word2vec/word2id.txt"
    pre_word2vec_path = "./word2vec/wiki_word2vec_50.bin"
    corpus_word2vec_path = "./word2vec/word_vec.txt"
    model_state_dict_path = "./model/sen_model.pkl"  # 模型保存位置
    best_model_path = "./model/sen_model_best.pkl"
    print('ok')

ok


In [64]:
from __future__ import unicode_literals, print_function, division
from io import open
import torch
import re
import pandas as pd
import numpy as np
import gensim
from torch.utils.data import Dataset
from hanziconv import HanziConv



class Data_set(Dataset):
    def __init__(self, Data, Label):
        self.Data = Data
        if Label is not None:  # 考虑对测试集的使用
            self.Label = Label

    def __len__(self):
        return len(self.Data)

    def __getitem__(self, index):
        if self.Label is not None:
            data = torch.from_numpy(self.Data[index])
            label = torch.from_numpy(self.Label[index])
            return data, label
        else:
            data = torch.from_numpy(self.Data[index])
            return data


def data_preview(file_path):
    """
    @description: preview the original data set: size, description info, etc.
    @param {*}
    - file_path: str, given the data file path.
    @return {*}
    - df: DataFrame, data in DataFrame format
    """
    with open(file_path, "r", encoding="utf-8") as f:
        data = []
        for line in f.readlines():
            sall = line.strip().split()
            if len(sall) < 2:  # 檢查行是否包含足夠的數據
                continue
            try:
                label = int(sall[0])  # 嘗試將第一個元素轉換為整數
                text = sall[1:]
                data.append([label, text])
            except ValueError:
                print(f"Skipping line due to ValueError: {line.strip()}")
                continue

    df = pd.DataFrame(data, columns=["label", "text"])
    print(
        "\n"
        + "*" * 20
        + " Original Data Description ("
        + file_path.split("/")[-1]
        + ")"
        + "*" * 20
        + "\n"
    )
    print("data length: ", len(data))
    print("data preview:\n", df.head())
    print("count label:\n", df["label"].value_counts())
    return df


def stopwordslist():  # 创建停用词表
    stopwords = [
        line.strip()
        for line in open(Config.stopword_path, encoding="UTF-8").readlines()
    ]
    return stopwords


def build_word2id(file):
    """
    @description: build the dict of 'word2id'
    @param {*}
    - file: str, word2id保存地址
    @return {*}
    返回word2id的字典
    """
    stopwords = stopwordslist()
    word2id = {"_PAD_": 0}
    path = [Config.train_path, Config.val_path]

    for _path in path:
        with open(_path, encoding="utf-8") as f:
            for line in f.readlines():
                out_list = []
                # 去停用词
                sp = line.strip().split()
                for word in sp[1:]:
                    if word not in stopwords:
                        rt = re.findall("[a-zA-Z]+", word)
                        if word != "\t":
                            # 去除长度为1的word
                            if len(rt) == 1:
                                continue
                            else:
                                out_list.append(word)
                for word in out_list:
                    if word not in word2id.keys():
                        word2id[word] = len(word2id)
    with open(file, "w", encoding="utf-8") as f:
        for w in word2id:
            f.write(w + "\t")
            f.write(str(word2id[w]))
            f.write("\n")
    return word2id


def build_id2word(word2id):
    """
    @description: 得到id2word
    @param {*}
    - word2id: dict, 字典word2id
    @return {*}
    - id2word: dict， 字典id2word
    """
    id2word = {}
    for key, val in word2id.items():
        id2word[val] = key
    return id2word


def build_word2vec(fname, word2id, save_to_path=None):
    """
    @description: 返回语料文本中词汇集对应的word2vec向量
    @param {*}
    - fname: str, 预训练的word2vec.
    - word2id: dict, 语料文本中包含的词汇集.
    - save_to_path: str, 保存训练语料库中的词组对应的word2vec到本地.
    @return {*}
    语料文本中词汇集对应的word2vec向量{id: word2vec}.
    """

    n_words = max(word2id.values()) + 1
    model = gensim.models.KeyedVectors.load_word2vec_format(fname, binary=True)
    print(type(model))
    word_vecs = np.array(np.random.uniform(-1.0, 1.0, [n_words, model.vector_size]))
    for word in word2id.keys():
        try:
            word_vecs[word2id[word]] = model[word]
        except KeyError:
            pass
    if save_to_path:
        with open(save_to_path, "w", encoding="utf-8") as f:
            for vec in word_vecs:
                vec = [str(w) for w in vec]
                f.write(" ".join(vec))
                f.write("\n")
    return word_vecs


def text_to_array(word2id, seq_lenth, path):
    """
    @description: 文本转为索引数字模式-将原始文本（包括标签和文本）里的每个词转为word2id对应的索引数字，并以数组返回.
    @param {*}
    - word2id: dict, 语料文本中包含的词汇集.
    - seq_length: int, 序列的限定长度.
    - path: str, 待处理的原始文本数据集.
    @return {*}
    返回原始文本转化索引数字数组后的数据集(array), 标签集(list).
    """
    label_array = []
    i = 0
    sa = []
    # 获取句子个数
    with open(path, encoding="utf-8") as f1:
        for l1 in f1.readlines():
            s = l1.strip().split()
            if len(s) < 2:  # 檢查行是否包含足夠的數據
                continue
            s1 = s[1:]
            new_s = [word2id.get(word, 0) for word in s1]  # 单词转索引数字
            sa.append(new_s)
    # 初始化句子数组
    with open(path, encoding="utf-8") as f:
        sentences_array = np.zeros(shape=(len(sa), seq_lenth))  # 行：句子个数 列：句子长度
        for line in f.readlines():
            sl1 = line.strip().split()
            if len(sl1) < 2:  # 檢查行是否包含足夠的數據
                continue
            sen = sl1[1:]
            new_sen = [word2id.get(word, 0) for word in sen]  # 单词转索引数字,不存在则为0
            new_sen_np = np.array(new_sen).reshape(1, -1)

            # 补齐每个句子长度，多余补零，少了就直接赋值,0填在前面。
            if np.size(new_sen_np, 1) < seq_lenth:
                sentences_array[i, seq_lenth - np.size(new_sen_np, 1) :] = new_sen_np[0, :]
            else:
                sentences_array[i, 0:seq_lenth] = new_sen_np[0, 0:seq_lenth]

            i += 1
            label = int(sl1[0])  # 标签
            label_array.append(label)
    return np.array(sentences_array), label_array

def text_to_array_sentence(word2id, seq_length, sentence):
    s = sentence.strip().split()
    # if len(s) < 2:  # 檢查句子長度
    #     raise ValueError("Sentence does not contain enough data.")
    
    # 繁體轉簡體
    trans_seq = HanziConv.toSimplified(s)

    # 詞轉index, 不存在為0
    new_sentence = [word2id.get(word, 0) for word in trans_seq]
    sentences_array = np.zeros(seq_length)  # 句子長度
    
    # padding, 0填在前面
    new_sen_np = np.array(new_sentence).reshape(1, -1)
    if np.size(new_sen_np, 1) < seq_length:
        sentences_array[seq_length - np.size(new_sen_np, 1):] = new_sen_np[0, :]
    else:
        sentences_array[0:seq_length] = new_sen_np[0, 0:seq_length]
    
    return sentences_array.reshape((1, -1))




def text_to_array_nolabel(word2id, seq_lenth, path):
    """
    @description: 文本转为索引数字模式-将原始文本（仅包括文本）里的每个词转为word2id对应的索引数字，并以数组返回.
    @param {*}
    - word2id: dict, 语料文本中包含的词汇集.
    - seq_length: int, 序列的限定长度.
    - path: str, 待处理的原始文本数据集.
    @return {*}
    原始文本转化索引数字数组后的数据集(array).
    """

    i = 0
    sa = []
    # 获取句子个数
    with open(path, encoding="utf-8") as f1:
        for l1 in f1.readlines():
            s = l1.strip().split()
            s1 = s[0:]  # s1=s[1:]
            new_s = [word2id.get(word, 0) for word in s1]  # 单词转索引数字
            sa.append(new_s)
    with open(path, encoding="utf-8") as f:
        sentences_array = np.zeros(shape=(len(sa), seq_lenth))  # 行：句子个数 列：句子长度
        for line in f.readlines():
            sl1 = line.strip().split()
            sen = sl1[0:]  # sen=sl1[1:]
            new_sen = [word2id.get(word, 0) for word in sen]  # 单词转索引数字,不存在则为0
            new_sen_np = np.array(new_sen).reshape(1, -1)
            if np.size(new_sen_np, 1) < seq_lenth:
                sentences_array[i, seq_lenth - np.size(new_sen_np, 1) :] = new_sen_np[
                    0, :
                ]
            else:
                sentences_array[i, 0:seq_lenth] = new_sen_np[0, 0:seq_lenth]
            i = i + 1
    return np.array(sentences_array)


def to_categorical(y, num_classes=None):
    """
    @description: 将类别转化为one-hot编码
    @param {*}
    - y: list, 类别特征的列表
    - num_class: int, 类别个数
    @return {*}
    返回one-hot编码数组,shape:（len(y), num_classes）
    """
    y = np.array(y, dtype="int")
    input_shape = y.shape
    if input_shape and input_shape[-1] == 1 and len(input_shape) > 1:
        input_shape = tuple(input_shape[:-1])
    y = y.ravel()
    if not num_classes:
        num_classes = np.max(y) + 1
    n = y.shape[0]
    categorical = np.zeros((n, num_classes))
    categorical[np.arange(n), y] = 1
    output_shape = input_shape + (num_classes,)
    categorical = np.reshape(categorical, output_shape)
    return categorical



def prepare_data(w2id, train_path, val_path, test_path, seq_lenth):
    """
    @description: 得到数字索引表示的句子和标签
    @param {*}
    - w2id: dict, 语料文本中包含的词汇集.
    - train_path: str, 训练数据集所在路径
    - val_path: str, 验证数据集所在路径
    - test_path: str, 测试数据集所在路径
    - seq_lenth: int, 序列的固定长度
    @return {*}
    - train_array: array, 训练集文本数组, shape:(len(train), seq_len)
    - train_label: array, 训练集标签数组, shape:(len(train), 1)
    - val_array: array, 验证集文本数组, shape:(len(val), seq_len)
    - val_label: array, 验证集标签数组, shape:(len(val), 1)
    - test_array: array, 测试集文本数组, shape:(len(test), seq_len)
    - test_label: array, 测试集标签数组, shape:(len(test), 1)
    """

    train_array, train_label = text_to_array(w2id, seq_lenth=seq_lenth, path=train_path)
    val_array, val_label = text_to_array(w2id, seq_lenth=seq_lenth, path=val_path)
    test_array, test_label = text_to_array(w2id, seq_lenth=seq_lenth, path=test_path)

    # 标签为[1, 1, 1, 1, 1, 1, 1, 1, 0, 0...]将标签转为onehot
    # train_label=to_categorical(train_label,num_classes=2)
    # val_label=to_categorical(val_label,num_classes=2)
    # print(train_lab,"\nval\n",val_lab)
    # """转换后标签
    #         [[0. 1.]
    #         [0. 1.]
    #         [0. 1.]
    #         ...
    #         [1. 0.]
    #         [1. 0.]
    #         [1. 0.]]"""

    train_label = np.array([train_label]).T
    val_label = np.array([val_label]).T
    test_label = np.array([test_label]).T

    return train_array, train_label, val_array, val_label, test_array, test_label


if __name__ == "__main__":
    # preview data
    train_df = data_preview(Config.train_path)
    val_df = data_preview(Config.val_path)
    test_df = data_preview(Config.test_path)
    

    # 建立word2id
    word2id = build_word2id(Config.word2id_path)

    # 建立id2word
    id2word = build_id2word(word2id)

    # 建立word2vec
    w2vec = build_word2vec(
        Config.pre_word2vec_path, word2id, Config.corpus_word2vec_path
    )

    # 得到句子id表示和标签
    (
        train_array,
        train_label,
        val_array,
        val_label,
        test_array,
        test_label,
    ) = prepare_data(
        word2id,
        train_path=Config.train_path,
        val_path=Config.val_path,
        test_path=Config.test_path,
        seq_lenth=Config.max_sen_len,
    )

    np.savetxt("./word2vec/train_data.txt", train_array, fmt="%d")
    np.savetxt("./word2vec/val_data.txt", val_array, fmt="%d")
    np.savetxt("./word2vec/test_data.txt", test_array, fmt="%d")
    np.savetxt("./word2vec/train_label.txt", train_label, fmt="%d")
    np.savetxt("./word2vec/val_label.txt", val_label, fmt="%d")
    np.savetxt("./word2vec/test_label.txt", test_label, fmt="%d")
    print("Data processing is complete.")



******************** Original Data Description (train.txt)********************

data length:  57470
data preview:
    label                                               text
0      1  [nan, 衣服, 快递, 速度, 有点, 意外, ，, 端午节, 送到, 的, ，, 本来...
1      1  [nan, 衣服, 还, 可以, ，, 很, 合身, ，, 十分满意, ，, 喜欢, 的, ...
2      0  [nan, 平板, 膜, 有, 瑕疵, ，, 能, 贴, ？, 至于, 外套, low, 死...
3      0  [这, 酒店, 太旧, 了, ,, 大厅, 看上去, 还, 可以, ., 房间, 的, 设施...
4      1  [nan, 书籍, 当, 我们, 看到, 别的, 孩子, 的, 优秀, 之处, 时, ，, ...
count label:
 label
1    28805
0    28665
Name: count, dtype: int64

******************** Original Data Description (val.txt)********************

data length:  8374
data preview:
    label                                               text
0      1  [nan, 洗发水, 一直, 在, 京东, 购物, ，, 实在, 太, 方便, 了, ，, ...
1      0  [nan, 衣服, 我选, 了, M, 号, 穿, 起来, 怎么, 还, 这么, 大, 衣服...
2      1  [房间, 舒适, ，, 环境, 不错, ，, 离, 火车站, 近, ，, 夜晚, 还是, 很...
3      0  [nan, 书籍, 一, 开始, 读, 的, 时候, 还, 觉得, 行, ，, 有模有样, ...
4      0  [nan, 衣服, 就是, 地摊货, 。, 没, 我, 在, 某,

In [65]:
from __future__ import unicode_literals, print_function, division
from io import open
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
from torch.utils.data import DataLoader, Dataset
import tqdm

from sklearn.metrics import confusion_matrix, f1_score, recall_score
import os


def train(train_dataloader, model, device, epoches, lr):

    model.train()
    model = model.to(device)

    print(model)
    optimizer = optim.Adam(model.parameters(), lr=lr)
    criterion = nn.CrossEntropyLoss()
    # 学习率调整
    # scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=10, gamma=0.2)
    best_acc = 0.85
    for epoch in range(epoches):
        train_loss = 0.0
        correct = 0
        total = 0

        train_dataloader = tqdm.tqdm(train_dataloader)
        # train_dataloader.set_description('[%s%04d/%04d %s%f]' % ('Epoch:', epoch + 1, epoches, 'lr:', scheduler.get_last_lr()[0]))
        for i, data_ in enumerate(train_dataloader):
            optimizer.zero_grad()
            input_, target = data_[0], data_[1]
            input_ = input_.type(torch.LongTensor)
            target = target.type(torch.LongTensor)
            input_ = input_.to(device)
            target = target.to(device)
            # 模型输出:output, shape:[num_samples, 2]
            # print(input_.shape)
            output = model(input_)
            # 实际目标label:target, shape:[num_samples, 1]=>[num_samples]
            target = target.squeeze(1)
            loss = criterion(output, target)
            loss.backward()
            optimizer.step()
            train_loss += loss.item()
            # get predicted label: Returns ``(values, indices)``
            _, predicted = torch.max(output, 1)
            total += target.size(0)
            correct += (predicted == target).sum().item()
            F1 = f1_score(target.cpu(), predicted.cpu(), average="weighted")
            Recall = recall_score(target.cpu(), predicted.cpu(), average="micro")
            # CM=confusion_matrix(target.cpu(),predicted.cpu())
            postfix = {
                "train_loss: {:.5f},train_acc:{:.3f}%"
                ",F1: {:.3f}%,Recall:{:.3f}%".format(
                    train_loss / (i + 1), 100 * correct / total, 100 * F1, 100 * Recall
                )
            }
            train_dataloader.set_postfix(log=postfix)

        acc = val_accuary(model, val_dataloader, device, criterion)

        if acc > best_acc:
            best_acc = acc
            if os.path.exists(Config.model_dir) == False:
                os.mkdir(Config.model_dir)
            torch.save(model, Config.best_model_path)

def val_accuary(model, val_dataloader, device, criterion=nn.CrossEntropyLoss()):
    """
    @description: get the accuracy of validation set
    @param {*}
    - model: Obeject, the Sentiment Analysis model (Seq2Seq).
    - val_dataloader: DataLoader, validation DataLoader
    - device: str, choose torch device {"cpu", "cuda"}
    - criterion: Object, criterion for calculating the loss, default=nn.CrossEntropyLoss()
    @return {*}
    val_accuracy: the accuracy of total validation set
    """
    model = model.to(device)
    with torch.no_grad():
        correct = 0  # 预测的和实际的label相同的样本个数
        total = 0  # 累计validation样本个数
        val_loss = 0.0
        for j, val_data in enumerate(val_dataloader, 0):
            input_val, target_val = val_data[0], val_data[1]
            input_val = input_val.type(torch.LongTensor)
            target_val = target_val.type(torch.LongTensor)
            target_val = target_val.squeeze(1)
            input_val = input_val.to(device)
            target_val = target_val.to(device)
            output_val = model(input_val)
            loss = criterion(output_val, target_val)
            val_loss += loss.item()
            _, pred_val = torch.max(output_val, 1)
            total += target_val.size(0)
            correct += (pred_val == target_val).sum().item()
            F1 = f1_score(target_val.cpu(), pred_val.cpu(), average="weighted")
            Recall = recall_score(target_val.cpu(), pred_val.cpu(), average="micro")
            CM = confusion_matrix(target_val.cpu(), pred_val.cpu())
        print(
            "\nVal accuracy : {:.3f}%, val_loss: {:.3f}, F1_score: {:.3f}%, Recall: {:.3f}%, Confusion_matrix: {}".format(
                100 * correct / total, val_loss, 100 * F1, 100 * Recall, CM
            )
        )
        return 100 * correct / total

if __name__ == "__main__":
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    # preview data
    train_df = data_preview(Config.train_path)
    test_df = data_preview(Config.test_path)
    val_df = data_preview(Config.val_path)
    # 建立word2id
    print(Config.word2id_path)
    word2id = build_word2id(Config.word2id_path)

    # 建立id2word
    id2word = build_id2word(word2id)

    # 得到句子表示和标签
    (
        train_array,
        train_label,
        val_array,
        val_label,
        test_array,
        test_label,
    ) = prepare_data(
        word2id,
        train_path=Config.train_path,
        val_path=Config.val_path,
        test_path=Config.test_path,
        seq_lenth=Config.max_sen_len,
    )

    # 生成word2vec
    w2vec = build_word2vec(Config.pre_word2vec_path, word2id, None)
    w2vec = torch.from_numpy(w2vec)
    w2vec = w2vec.float()  # CUDA接受float32，不接受float64

    # build datalaoder
    train_loader = Data_set(train_array, train_label)
    train_dataloader = DataLoader(
        train_loader, batch_size=Config.batch_size, shuffle=True, num_workers=0
    )  # 用了workers反而变慢了

    val_loader = Data_set(val_array, val_label)
    val_dataloader = DataLoader(
        val_loader, batch_size=Config.batch_size, shuffle=True, num_workers=0
    )

    test_loader = Data_set(test_array, test_label)
    test_dataloader = DataLoader(
        test_loader, batch_size=Config.batch_size, shuffle=True, num_workers=0
    )

    # build model
    model = LSTM_attention(
        Config.vocab_size,
        Config.embedding_dim,
        w2vec,
        Config.update_w2v,
        Config.hidden_dim,
        Config.num_layers,
        Config.drop_keep_prob,
        Config.n_class,
        Config.bidirectional,
    )

    # 模型训练
    train(
        train_dataloader,
        model=model,
        device=device,
        epoches=Config.n_epoch,
        lr=Config.lr,
    )

    # 保存模型
    """if os.path.exists(Config.model_dir) == False:
        os.mkdir(Config.model_dir)
    torch.save(model, Config.model_state_dict_path)
    """


******************** Original Data Description (train.txt)********************

data length:  57470
data preview:
    label                                               text
0      1  [nan, 衣服, 快递, 速度, 有点, 意外, ，, 端午节, 送到, 的, ，, 本来...
1      1  [nan, 衣服, 还, 可以, ，, 很, 合身, ，, 十分满意, ，, 喜欢, 的, ...
2      0  [nan, 平板, 膜, 有, 瑕疵, ，, 能, 贴, ？, 至于, 外套, low, 死...
3      0  [这, 酒店, 太旧, 了, ,, 大厅, 看上去, 还, 可以, ., 房间, 的, 设施...
4      1  [nan, 书籍, 当, 我们, 看到, 别的, 孩子, 的, 优秀, 之处, 时, ，, ...
count label:
 label
1    28805
0    28665
Name: count, dtype: int64

******************** Original Data Description (test.txt)********************

data length:  16256
data preview:
    label                                               text
0      1  [nan, 水果, 苹果, 不错, ，, 京东, 购买, 方便快捷, ，, 没有, 坏, 的...
1      0  [nan, 衣服, 不想, 说, 了, ，, 这, 裤子, ，, 我, 还, 不如, 去, ...
2      1  [nan, 水果, 还, 行, ，, 脆脆, 的, ，, 甜, 的, ，, 不红, 的, 果...
3      0                         [为, 都, 是, 肥肉, ！, nan, nan]
4      0  [5, 。, 1, 。, ---, 5, 。, 3, 。, 入

100%|██████████| 898/898 [00:13<00:00, 64.97it/s, log={'train_loss: 0.52348,train_acc:70.550%,F1: 90.312%,Recall:90.323%'}]



Val accuracy : 85.765%, val_loss: 45.324, F1_score: 76.000%, Recall: 75.926%, Confusion_matrix: [[22  8]
 [ 5 19]]


100%|██████████| 898/898 [00:13<00:00, 68.93it/s, log={'train_loss: 0.29766,train_acc:88.350%,F1: 77.419%,Recall:77.419%'}]  



Val accuracy : 89.682%, val_loss: 34.696, F1_score: 88.827%, Recall: 88.889%, Confusion_matrix: [[28  2]
 [ 4 20]]


...


Val accuracy : 90.076%, val_loss: 33.061, F1_score: 90.809%, Recall: 90.741%, Confusion_matrix: [[21  1]
 [ 4 28]]


100%|██████████| 898/898 [00:12<00:00, 70.45it/s, log={'train_loss: 0.24084,train_acc:90.889%,F1: 95.165%,Recall:95.161%'}]  



Val accuracy : 91.032%, val_loss: 30.757, F1_score: 92.603%, Recall: 92.593%, Confusion_matrix: [[24  1]
 [ 3 26]]


100%|██████████| 898/898 [00:12<00:00, 70.34it/s, log={'train_loss: 0.22625,train_acc:91.489%,F1: 90.364%,Recall:90.323%'}]  



Val accuracy : 90.865%, val_loss: 30.791, F1_score: 88.919%, Recall: 88.889%, Confusion_matrix: [[25  5]
 [ 1 23]]


### 評估模型

In [66]:
def test_accuracy(model, test_dataloader, device):
    """
    @description: get the accuracy of test set
    @param {*}
    - model: Obeject, the Sentiment Analysis model (Seq2Seq).
    - test_dataloader: DataLoader, test DataLoader
    - device: str, choose torch device {"cpu", "cuda"}
    @return {*}
    test_accuracy: the accuracy of total test set
    """
    model = model.to(device)
    with torch.no_grad():
        label, output = [], []
        for k, data_test in enumerate(test_dataloader, 0):
            input_test, target_test = data_test[0], data_test[1]
            input_test = input_test.type(torch.LongTensor)
            target_test = target_test.type(torch.LongTensor)
            target_test = target_test.squeeze(1)
            input_test = input_test.to(device)
            target_test = target_test.to(device)
            output_test = model(input_test)
            print(input_test)
            _, pred_test = torch.max(output_test, 1)

            label.append(target_test.cpu())
            output.append(pred_test.cpu())
        label = torch.cat(label, dim=0)
        output = torch.cat(output, dim=0)

        total = label.size(0)
        correct = (label == output).sum().item()

        F1 = f1_score(label, output, average="weighted")
        Recall = recall_score(label, output, average="micro")
        CM = confusion_matrix(label, output)
        print(
            "\nTest accuracy : {:.3f}%, F1_score: {:.3f}%, Recall: {:.3f}%, Confusion_matrix: {}".format(
                100 * correct / total, 100 * F1, 100 * Recall, CM/CM.sum()
            )
        )

def pre(word2id, model, seq_lenth, path, test_array, test_label):
    model.cpu()
    with open(path, "r", encoding="utf-8") as f:
        texts = f.readlines()
    with torch.no_grad():
        sen_p = torch.from_numpy(test_array)
        sen_p = sen_p.type(torch.LongTensor)
        output_p = model(sen_p)
        _, pred = torch.max(output_p, 1)
        for i in range(pred.size(0)):
            print(
                "\nitem: {}, {}, => 預測類別為 =>, {}\n".format(
                    i + 1, texts[i], pred[i].item()
                )
            )


# 預測
pre(word2id, model, Config.max_sen_len, Config.test_path, test_array, test_label)

# 測試
test_accuracy(model, test_dataloader, device)



item: 1, 1   nan   水果   苹果 不错 ， 京东 购买 方便快捷 ， 没有 坏 的 ， 质量 可以 。
, => 預測類別為 =>, 1


item: 2, 0   nan   衣服   不想 说 了 ， 这 裤子 ， 我 还 不如 去 买 地摊货 呢 ！
, => 預測類別為 =>, 0


item: 3, 1   nan   水果   还 行 ， 脆脆 的 ， 甜 的 ， 不红 的 果 不 好吃 ， 苦
, => 預測類別為 =>, 1


item: 4, 0   为 都 是 肥肉 ！   nan   nan
, => 預測類別為 =>, 0


item: 5, 0   5 。 1 。 --- 5 。 3 。 入住 一直 没敢 在 房间 洗澡 。 太冷 。 房间 太 陈旧 。 设施 太 差 。 房间 里 提供 桶装水 还单 收费   nan   nan
, => 預測類別為 =>, 0


item: 6, 0   房间 干净 ， 但 加床 后 无法 动弹 ， 设施 有 二星 水平 ， 在 山上 算 不错 了 。 房间 只配 二件 羽绒服 ， 加床 小孩 必须 挨冻 能力 极强 ， 前台 无法 商量 ， 260 元 / 天 只是 加床 费用 ， 不 含 羽绒服 。 餐厅 绝对 是 五星 的 价格 ， 二星 的 服务 。   nan   nan
, => 預測類別為 =>, 1


item: 7, 0   nan   洗发水   妈 的 ， 买贵 了 ， 就 这 两天 降 了 *
, => 預測類別為 =>, 0


item: 8, 1   nan   书籍   购买 此书 是 经过 朋友 推荐 ， 买回来 觉得 非常 不错 。 我家 女儿 5 岁 ， 比较 喜欢 科普 图书 ， 这 套书 目前 是 她 比较 喜欢 的 图书 ， 每天 都 要 和 我 一 起来 分享 各种 有趣 的 知识 ， 现在 在 看 生物 篇 ， 对 其中 的 鲸 特别 有 兴趣 。 个人 觉得 这 套书 合适 小学 低年级 小朋友 阅读 ， 幼儿园 的 小朋友 可能 需要 家长 陪同 阅读 ， 对 大人 和 小孩 来讲 都 非常 长 知识 ， 非常 不错 ， 赞 一个 !
, => 預測類別為 =>, 1


item: 9, 0   nan   酒店  

## PC1

In [67]:
import torch
import jieba

def predict_sentiment_PC1(sentence, model, word2id, max_sequence_length, device='cpu'):
    # Ensure the model is in evaluation mode
    model.eval()

    # Ensure the model is on the right device
    model.to(device)

    # Process the sentence
    sentence = ' '.join(jieba.lcut(sentence, cut_all=False, HMM=True))
    sequence_array = text_to_array_sentence(word2id, max_sequence_length, sentence)
    
    # Ensure the input tensor is on the right device
    input_tensor = torch.tensor(sequence_array, dtype=torch.long).to(device)

    with torch.no_grad():
        output = model(input_tensor)

    _, result = torch.max(output[0], dim=0)
    sentiment = 'Positive' if result.item() == 1 else 'Negative'
    return sentiment

# Usage
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
sentence = '帥哦！大家一起推動打垮藍綠，讓台/灣往前走'
max_sequence_length = 100
sentiment = predict_sentiment_PC1(sentence, model, word2id, max_sequence_length, device)
print("Sentiment:", sentiment)


Sentiment: Positive


In [68]:
emotions_model_PC_1 = []
for i in final["message_content"]:
    test_sentence = i
    max_sequence_length = 100
    emotion = -1 if predict_sentiment_PC1(test_sentence, model, word2id, max_sequence_length) == "Negative" else 1
    emotions_model_PC_1.append(emotion)
    #print(f"Sentence: '{test_sentence}' -> Sentiment: {predict_sentiment(test_sentence, model, tokenizer, max_sequence_length)}")



In [81]:
final_with_PC1 = final.copy()
final_with_PC1["Bi-LSTM_emotions"] = emotions_model_PC_1
final_with_PC1

userid             time  \
0                             bybe  (10/01, 11, 46)   
1                           spzper  (10/01, 11, 46)   
2                         tchialen  (10/01, 11, 46)   
3                      IamHsihPing  (10/01, 11, 46)   
4                          a210510  (10/01, 11, 46)   
...                            ...              ...   
8831               ice80712 (打臉腦粉)  (11/21, 09, 33)   
8832              sunyeah (   湯元嗎)  (11/21, 17, 32)   
8833  chopper594 (世界のももクロ No.1!!!)  (11/21, 17, 34)   
8834               slamguyno1 (布魯)  (11/21, 18, 11)   
8835                    A6 (短ID真好)  (11/21, 18, 31)   

                                        message_content  push_tag  \
0                                                               1   
1                                            抓到國昌挺中共同路3         0   
2                                           中共同路人挺中共同路人         0   
3                                               柯韓昌粉一家親         0   
4                                               抓到國師挺柯p         0   
...                                                 ...       ...   
8831  所以黃國昌有當兵嗎? 時代力量支持者常常說民進黨抗中保台是假的，騙票是真的， 時代力量才是真...         0   
8832  加入33團隊的話 那如果黃珊珊當選台北市長的話 黃國昌可以接任法務局長吧 副市長應該不太適合...         0   
8833  : 新頭殼 : 邱于真 : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情...         0   
8834  : 加入33團隊的話 : 那如果黃珊珊當選台北市長的話 : 黃國昌可以接任法務局長吧 : 副...         0   
8835  : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情 : 九合一選戰進入倒數...         0   

                      article_title keyword                        author  \
0     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
1     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
2     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
3     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
4     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
...                             ...     ...                           ...   
8831  Re: [新聞] 現身挺黃珊珊！黃國昌：抗中保台是全民DN     黃國昌               ice80712 (打臉腦粉)   
8832   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌              sunyeah (   湯元嗎)   
8833   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌  chopper594 (世界のももクロ No.1!!!)   
8834   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌               slamguyno1 (布魯)   
8835   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌                    A6 (短ID真好)   

      Bi-LSTM_emotions  
0                   -1  
1                    1  
2                    1  
3                   -1  
4                    1  
...                ...  
8831                -1  
8832                -1  
8833                 1  
8834                -1  
8835                 1  

[8836 rows x 8 columns]

# 資料分析－code

In [45]:
push_tag_counts = final.groupby(['userid', 'push_tag']).size().unstack(fill_value=0)

# 找到各種類型(push_tag)次數最多的前三名用戶
top_users = {}
for push_tag in push_tag_counts.columns:
    top_3_users = push_tag_counts[push_tag].nlargest(3).index.tolist()
    top_users[push_tag] = top_3_users

# 收集這三名(共9名)用戶的個別使用push_tag的次數
unique_top_users = set([user for users in top_users.values() for user in users])
user_push_tag_dict = {userid: push_tag_counts.loc[userid].to_dict() for userid in unique_top_users}

print("各種類型次數最多的前三名用戶:", top_users)
print("這些用戶的個別使用push_tag的次數:", user_push_tag_dict)

各種類型次數最多的前三名用戶: {-1: ['JT0624', 'bybe', 'coffee112'], 0: ['coffee112', 'Newtype', 'lmf770410'], 1: ['akirakid', 'stvn2567', 'lmf770410']}
這些用戶的個別使用push_tag的次數: {'JT0624': {-1: 6, 0: 3, 1: 4}, 'akirakid': {-1: 0, 0: 13, 1: 30}, 'lmf770410': {-1: 2, 0: 15, 1: 21}, 'Newtype': {-1: 4, 0: 18, 1: 13}, 'stvn2567': {-1: 2, 0: 12, 1: 25}, 'coffee112': {-1: 5, 0: 22, 1: 9}, 'bybe': {-1: 6, 0: 12, 1: 15}}


In [46]:
# 記錄每個用戶的push_tag次數
push_tag_counts = final.groupby(['userid', 'push_tag']).size().unstack(fill_value=0)

# 計算每個用戶的push_tag總次數和1, -1的使用比率
push_tag_counts['total'] = push_tag_counts.sum(axis=1)
push_tag_counts['ratio_1'] = push_tag_counts[1.0] / push_tag_counts['total']
push_tag_counts['ratio_minus_1'] = push_tag_counts[-1.0] / push_tag_counts['total']

# 設定次數門檻
threshold = 10

# 找到push_tag為1和-1次數最多的前三名用戶
top_users_1 = push_tag_counts[1.0].nlargest(3)
top_users_minus_1 = push_tag_counts[-1.0].nlargest(3)

# 找到push_tag為1和-1使用比率最高且次數大於門檻的前三名用戶
top_ratio_users_1 = push_tag_counts[push_tag_counts[1.0] > threshold]['ratio_1'].nlargest(3)
top_ratio_users_minus_1 = push_tag_counts[push_tag_counts[-1.0] > threshold]['ratio_minus_1'].nlargest(3)

# 輸出結果
print(f"關鍵詞為 {keywords_to_search[0]} 時的情況: \n")
print("push_tag為1次數最多的前三名用戶:")
for user, count in top_users_1.items():
    print(f"{user}: 次數={count}, 比例={push_tag_counts.loc[user, 'ratio_1']:.2f}")

print("\npush_tag為-1次數最多的前三名用戶:")
for user, count in top_users_minus_1.items():
    print(f"{user}: 次數={count}, 比例={push_tag_counts.loc[user, 'ratio_minus_1']:.2f}")

print("\npush_tag為1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in top_ratio_users_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={push_tag_counts.loc[user, 1.0]}")

print("\npush_tag為-1使用比率最高且次數大於門檻的前三名用戶:")
if len(top_ratio_users_minus_1) == 0:
    print("沒有超過thershold的留言數量!")
for user, ratio in top_ratio_users_minus_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={push_tag_counts.loc[user, -1.0]}")

關鍵詞為 黃國昌 時的情況: 

push_tag為1次數最多的前三名用戶:
akirakid: 次數=30, 比例=0.70
stvn2567: 次數=25, 比例=0.64
lmf770410: 次數=21, 比例=0.55

push_tag為-1次數最多的前三名用戶:
JT0624: 次數=6, 比例=0.46
bybe: 次數=6, 比例=0.18
coffee112: 次數=5, 比例=0.14

push_tag為1使用比率最高且次數大於門檻的前三名用戶:
porfavor: 比例=0.85, 次數=11
turbomons: 比例=0.71, 次數=12
akirakid: 比例=0.70, 次數=30

push_tag為-1使用比率最高且次數大於門檻的前三名用戶:
沒有超過thershold的留言數量！


In [117]:
#push_tag_counts
row_sums = push_tag_counts.sum(axis=0)
row_sums

push_tag
-1                934.000000
0                4881.000000
1                3021.000000
total            8836.000000
ratio_1          1306.781825
ratio_minus_1     469.186832
dtype: float64

In [112]:
final_push_tag = final.copy()
final_push_tag.pop('keyword')
final_push_tag.pop('time')
final_push_tag["LSTM_emotions"] = eomtions_model_TC_1
final_push_tag["RF_emotions"] = emotions_model_TC_2
final_push_tag["Bi-LSTM_emotions"] = emotions_model_PC_1
push_tag_user = useridSearch('akirakid', final_push_tag)
push_tag_user

userid                                    message_content  push_tag  \
1732  akirakid                      靠北，我還想說美女醫誰啊點進來/直接寫基進的誰我就會無視了         1   
1854  akirakid                      時力要支持哪個候選人，不是黃國昌說了/就能代表時力支持吧。         1   
2390  akirakid                                         羨慕！我們新北...         0   
2397  akirakid                                  所以藍綠取得權力之後往哪邊倒了呢？         0   
2403  akirakid                          不然呢？當一席立委當一席議員藍綠的多/數誰鳥你呢？         1   
2418  akirakid        黃國昌他指的是基隆選區吧，他踢爆的國/家賤賣土地給黑道藍綠市長候選人都有去/黑道生日宴         1   
2423  akirakid                                       退黨的祝福啊，不然怎麼辦         0   
2428  akirakid                                 時代力量基隆有推其它議員候選人，3個         0   
2431  akirakid  如果他做不好，那沒了也沒什麼可惜，如/果他做的好，那其實跟黃國昌一樣，黃國/昌說他一個人在國...         1   
2433  akirakid  貧窮的小黨拿出錢和資源來選市長不是容/易的事，也許是錯，但是我覺得他做的好/或不好，應該比那...         1   
2436  akirakid  如果覺得別人別黨藍綠好的，就去投自己/喜歡的就好，如果覺得他做的好就投他給/他一個機會就好了...         1   
2438  akirakid                                 支持藻礁到最後的，多的是初期喊支持之         1   
2441  akirakid                                           後閉嘴的，他不是         1   
2445  akirakid              選後當側翼的話我幹嘛還看到一堆人貼鏡/電視調閱小組投票時陳椒華主席跟國民黨         1   
2447  akirakid                                               投支持票         1   
2451  akirakid                     如果沒有增加夥伴，連黨團都沒有，也沒/辦法提案，只能努力掙脫         1   
2455  akirakid                    https://i.imgur.com/oL4NAij.jpg         1   
2457  akirakid  我覺得沒有他做的好不好，只有小綠和選/市長錯誤，是因為覺得他威脅藍綠的選票/，那我會認為他只...         1   
2460  akirakid  我覺得是給一個藍綠之外的選擇，和突破/困境的努力，繼續現狀最好不過就是像黃/國昌說的一個人在...         1   
2463  akirakid                                     我覺得那就是一堆爛蘋果的例子         1   
2466  akirakid         所以我比較覺得是威脅到別黨的票，少數/小黨在國會議會面對大黨或地方勢力，我/想不好過         1   
2469  akirakid                            主張打倒炒房仔的政黨？零號候選人好像/沒有政黨         1   
2471  akirakid                    https://i.imgur.com/mXDzNCf.jpg         0   
2473  akirakid  Ours的洛書剛寫完書，名叫無住之島，吹/哨揭弊者保護協會就黃國昌辦的，公民幫/推我就不曉得...         1   
2477  akirakid                               Ours跟黃國昌一直有合作推囤房稅，到椒         0   
2479  akirakid                                    華主席年代我記得還有在推相關的         0   
2483  akirakid                                            基隆有白能選？         1   
2487  akirakid                  所以對那些退黨的我都真心感謝帶祝福/能離開時力去抗中保台真是太好了         1   
2489  akirakid           我自己認為時力黨中央對陳椒華主席的認/同和支持態度是有在維護時力自己路線的/力量         1   
2491  akirakid              苗栗兩個無黨籍的直接跑去當徐定禎發言/人，一個回頭攻擊宋國鼎，我覺得還在時         1   
2493  akirakid  力黨裡的多少還是會有一些受黨羈縻的態/度，一開始的那兩個不分區我覺得或許創/黨時期的時力就是...         1   
2500  akirakid                 基隆有民眾黨選市長？沒有的話是在講什/麼？/還是爛蘋果裝白蘋果來噓？         1   
2506  akirakid  時代力量洗過一輪之後，你看現在競選總/部成立黃國昌會到的，會去吹哨者協會辦/的活動的，就知道...         1   
2508  akirakid                          比起來我比較羨慕能對自己投的候選人那/麼有信心的人         1   
2514  akirakid                                 投票又不是買彩券，會中的才要買 XD         1   
2515  akirakid  如果覺得他不夠好，那選不上也不是什麼/問題，如果比較好，那就買一個機會/畢竟不好的選上還是從...         1   
2554  akirakid                                        你的白色側翼標準很低呢         0   
2932  akirakid                                                 高调         0   
3300  akirakid                                                 高調         0   
3720  akirakid                                                 高調         0   
4432  akirakid                                                 高調         1   
5413  akirakid                                                 高調         0   
8806  akirakid                                                 高調         0   

                       article_title                        author  \
1732  Re: [新聞] 黃國昌喊票投黃珊珊 美女醫驚爆2014年兩                   ffdqfe (苦惱)   
1854        [新聞] 黃國昌表態支持黃珊珊 陳椒華：不代表時                 OGCOGCOGC (0)   
2390         [新聞] 時代力量陳薇仲競選總部成立　黃國昌：               DESW1 (說話很慢的大叔)   
2397         [新聞] 時代力量陳薇仲競選總部成立　黃國昌：               DESW1 (說話很慢的大叔)   
2403         [新聞] 時代力量陳薇仲競選總部成立　黃國昌：               DESW1 (說話很慢的大叔)   
2418         [新聞] 時代力量陳薇仲競選總部成立　黃國昌：               DESW1 (說話很慢的大叔)   
2423         [新聞] 時代力量陳薇仲競選總部成立　黃國昌：     

In [82]:
final_with_all = final.copy()
final_with_all["LSTM_emotions"] = eomtions_model_TC_1
final_with_all["RF_emotions"] = emotions_model_TC_2
final_with_all["Bi-LSTM_emotions"] = emotions_model_PC_1
final_with_all

userid             time  \
0                             bybe  (10/01, 11, 46)   
1                           spzper  (10/01, 11, 46)   
2                         tchialen  (10/01, 11, 46)   
3                      IamHsihPing  (10/01, 11, 46)   
4                          a210510  (10/01, 11, 46)   
...                            ...              ...   
8831               ice80712 (打臉腦粉)  (11/21, 09, 33)   
8832              sunyeah (   湯元嗎)  (11/21, 17, 32)   
8833  chopper594 (世界のももクロ No.1!!!)  (11/21, 17, 34)   
8834               slamguyno1 (布魯)  (11/21, 18, 11)   
8835                    A6 (短ID真好)  (11/21, 18, 31)   

                                        message_content  push_tag  \
0                                                               1   
1                                            抓到國昌挺中共同路3         0   
2                                           中共同路人挺中共同路人         0   
3                                               柯韓昌粉一家親         0   
4                                               抓到國師挺柯p         0   
...                                                 ...       ...   
8831  所以黃國昌有當兵嗎? 時代力量支持者常常說民進黨抗中保台是假的，騙票是真的， 時代力量才是真...         0   
8832  加入33團隊的話 那如果黃珊珊當選台北市長的話 黃國昌可以接任法務局長吧 副市長應該不太適合...         0   
8833  : 新頭殼 : 邱于真 : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情...         0   
8834  : 加入33團隊的話 : 那如果黃珊珊當選台北市長的話 : 黃國昌可以接任法務局長吧 : 副...         0   
8835  : 黃國昌宣布加入黃珊珊團隊 學者沈榮欽：重創時代力量台北市議員選情 : 九合一選戰進入倒數...         0   

                      article_title keyword                        author  \
0     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
1     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
2     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
3     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
4     [新聞] 第三勢力整合　黃國昌挺黃珊珊：若是市民一定投給她     黃國昌                  WuSam (藤原豆海)   
...                             ...     ...                           ...   
8831  Re: [新聞] 現身挺黃珊珊！黃國昌：抗中保台是全民DN     黃國昌               ice80712 (打臉腦粉)   
8832   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌              sunyeah (   湯元嗎)   
8833   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌  chopper594 (世界のももクロ No.1!!!)   
8834   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌               slamguyno1 (布魯)   
8835   Re: [新聞] 黃國昌宣布「加入黃珊珊團隊」 學者沈榮     黃國昌                    A6 (短ID真好)   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
0                 1           0                -1  
1                 1           0                 1  
2                -1           0                 1  
3                -1           0                -1  
4                 1           0                 1  
...             ...         ...               ...  
8831              1        -1.0                -1  
8832             -1        -1.0                -1  
8833             -1        -1.0                 1  
8834              1        -1.0                -1  
8835             -1        -1.0                 1  

[8836 rows x 10 columns]

In [84]:
# 記錄每個用戶的情緒次數
emotion_counts_TC1 = final_with_TC1.groupby(['userid', 'LSTM_emotions']).size().unstack(fill_value=0)
#print(emotion_counts)
# 計算每個用戶的emotion總次數和1, -1的使用比率
emotion_counts_TC1['total'] = emotion_counts_TC1.sum(axis=1)
emotion_counts_TC1['ratio_1'] = emotion_counts_TC1[1.0] / emotion_counts_TC1['total']
emotion_counts_TC1['ratio_minus_1'] = emotion_counts_TC1[-1.0] / emotion_counts_TC1['total']

# 設定次數門檻
threshold = 10

# 找到emotion為1和-1次數最多的前三名用戶
emotion_top_users_1 = emotion_counts_TC1[1.0].nlargest(3)
emotion_top_users_minus_1 = emotion_counts_TC1[-1.0].nlargest(3)

# 找到emotion為1和-1使用比率最高且次數大於門檻的前三名用戶
emotion_top_ratio_users_1 = emotion_counts_TC1[emotion_counts_TC1[1.0] > threshold]['ratio_1'].nlargest(3)
emotion_top_ratio_users_minus_1 = emotion_counts_TC1[emotion_counts_TC1[-1.0] > threshold]['ratio_minus_1'].nlargest(3)

#輸出現在使用的模型
print("使用LSTM得到的emotions: \n")

# 輸出結果
print("emotion為1次數最多的前三名用戶:")
for user, count in emotion_top_users_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts_TC1.loc[user, 'ratio_1']:.2f}")

print("\nemotion為-1次數最多的前三名用戶:")
for user, count in emotion_top_users_minus_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts_TC1.loc[user, 'ratio_minus_1']:.2f}")

print("\nemotion為1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts_TC1.loc[user, 1.0]}")

print("\nemotion為-1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_minus_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts_TC1.loc[user, -1.0]}")

使用LSTM得到的emotions: 

emotion為1次數最多的前三名用戶:
akirakid: 次數=28, 比例=0.65
coffee112: 次數=19, 比例=0.53
lmf770410: 次數=14, 比例=0.37

emotion為-1次數最多的前三名用戶:
neoa01: 次數=27, 比例=0.87
stvn2567: 次數=25, 比例=0.64
lmf770410: 次數=24, 比例=0.63

emotion為1使用比率最高且次數大於門檻的前三名用戶:
smonkey: 比例=1.00, 次數=11
shi21: 比例=0.92, 次數=11
lasekoutkast: 比例=0.75, 次數=12

emotion為-1使用比率最高且次數大於門檻的前三名用戶:
tsungmou: 比例=0.93, 次數=13
neoa01: 比例=0.87, 次數=27
abc55643: 比例=0.87, 次數=20


In [122]:
row_sums_TC1 = emotion_counts_TC1.sum(axis=0)
row_sums_TC1

LSTM_emotions
-1               4681.000000
1                4155.000000
total            8836.000000
ratio_1          1983.289418
ratio_minus_1    2129.710582
dtype: float64

In [114]:
emotion_user = useridSearch('shi21',final_with_all)
emotion_user

userid         message_content  push_tag  LSTM_emotions RF_emotions  \
518   shi21                      加油         0              1           0   
1024  shi21                       推         0              1           0   
1933  shi21               蔡英文繼續裝死中啦         0              1        -1.0   
2366  shi21                     推33         0              1           0   
3273  shi21                     推國昌         0              1           0   
3788  shi21                       推         1              1           0   
3981  shi21                    黑道治國         0              1        -1.0   
4357  shi21                    黑道治國         0              1        -1.0   
4794  shi21  ------天道盟太陽會-----  幫高調         0              1           0   
5397  shi21                       推         0              1           0   
6794  shi21                       推         1              1           0   
8219  shi21                 這學者又是誰啊         1             -1           0   

      Bi-LSTM_emotions  
518                 -1  
1024                -1  
1933                -1  
2366                -1  
3273                -1  
3788                -1  
3981                -1  
4357                -1  
4794                -1  
5397                -1  
6794                -1  
8219                -1

In [110]:
#黃國昌的死忠黑粉
emotion_user = useridSearch('widec',final_with_all)
emotion_user

userid                         message_content  push_tag  LSTM_emotions  \
1263  widec                   會參加基進黨的是什麼咖 你自己也知道 呵呵        -1              1   
1642  widec                             一個女的去加什麼雞雞黨         0              1   
2075  widec                    黃珊珊才是正常的市長候選人 可惜台灣不配         0             -1   
2078  widec                         台灣人注定只看血統、黨派、藍綠         1             -1   
2085  widec                         覺青潑起髒水還比老人嫻熟老練哩         0             -1   
2087  widec                      真的是知識拋兩邊，情緒上腦，鬥爭第一         0             -1   
2093  widec                   對阿 也不是蔣萬安差 只是黃珊珊有完整歷練         0              1   
3017  widec                      我只知道我認識的塔綠班朋友超恨黃國昌         1             -1   
3026  widec                   上立委也沒用啊 他被完全封殺 只能狗吠火車         0              1   
5864  widec                             就東堂勇亂搞白道勢力啊         0             -1   
6277  widec  笑死 你把國昌粉看得這麼腦殘跟低賤嗎/呃 我是指第一段說這些話的人 XDDD         1             -1   
6542  widec                          抗中保台是根本連講都不用講的         1              1   
6544  widec                       戰事一開 誰能不抗中 誰能不保台？         1             -1   
7480  widec                                明明是受益最多的         0             -1   
8375  widec                                                 1              1   
8426  widec                   怎不敢寫張益贍因為負面醜聞被TMD開除黨籍        -1             -1   
8438  widec                     前柯幕僚(x) 連柯都不要的幕僚(o)        -1             -1   
8691  widec                          黃國昌之前也沒表態支持民眾黨         0             -1   
8780  widec                              想告贏黃國昌很難很難         1             -1   
8784  widec                           黃國昌又沒選，哪來的沒當選         0              1   

     RF_emotions  Bi-LSTM_emotions  
1263         1.0                 1  
1642           0                -1  
2075         1.0                -1  
2078           0                -1  
2085           0                -1  
2087        -1.0                -1  
2093         1.0                -1  
3017        -1.0                -1  
3026        -1.0                -1  
5864           0                 1  
6277           0                -1  
6542           0                -1  
6544           0                -1  
7480           0                 1  
8375           0                -1  
8426        -1.0                -1  
8438        -1.0                -1  
8691           0                 1  
8780           0                 1  
8784           0                -1

In [111]:
emotion_user = useridSearch('neoa01',final_with_all)
emotion_user

userid                                    message_content  push_tag  \
130   neoa01                                黃國昌還是省省吧，風向大師，看看自己在         0   
133   neoa01                                          立院的表決倒哪邊？         0   
2028  neoa01                        民進黨不倒，選舉風氣不會好/黃國昌不能勇敢講民進黨嗎？         1   
2386  neoa01            黃國昌的話一點都沒有可信力，看看台灣人/想擺脫藍綠，你們取得權力後，向哪邊倒？         1   
2388  neoa01                        立院表決真是令台灣人失望，更別說你自己/之前挺那個人了         1   
2544  neoa01  選舉當然是選會上的，沒上的等於浪費選票/不然你還敢讓民進黨執政嗎/票投小黨=保送民進黨，20...         1   
2661  neoa01                               可是民進黨提名的，你如果能投  難道你不        -1   
2663  neoa01                                             會投他嗎xD         1   
3083  neoa01                                反正你還是票投小英民進黨啦，你在立院投         0   
3085  neoa01                                           票的表現不彎腰嗎         1   
3920  neoa01  台灣治安惡化、警界沉淪，不知道跟小英民/進黨的作風有沒有關聯/https://i.imgur...         1   
4031  neoa01                    https://i.imgur.com/fbaGQWo.jpg         1   
4297  neoa01  民進黨執政意外嗎？難怪治安惡化成這樣/https://i.imgur.com/fbaGQWo...         1   
4515  neoa01                       民進黨不倒，台灣先倒/台灣生不如死，民進黨經濟20來最好         1   
5414  neoa01                                        勤政 清廉 愛鄉土 ？         0   
5420  neoa01                    https://i.imgur.com/fbaGQWo.jpg         0   
5430  neoa01  黃國昌側面了解後表示，「調查局」早已立/案調查郭哲敏集團犯行，但「警方提前」一/步發動搜索。...         1   
5482  neoa01        2020 let’s win, tw lose./台灣生不如死，民進黨經濟20年來最好         1   
5499  neoa01                       當然要扯藍綠啊，/完全執政綠色的問題扯藍就對了，分掉藍色         1   
5501  neoa01                                  的票、死忠綠跑不掉，就是保送民進黨         0   
5522  neoa01                    https://i.imgur.com/C3IN2fp.jpg         0   
5947  neoa01                                講到黃國昌 他支持的就沒什麼可以看的。         0   
5949  neoa01  看看他之前挺小英，民進黨把台灣害成什麼/樣，少子化、能源、高房價、治安交通爛，/檢警調司法崩...         1   
6355  neoa01                                黃國昌講話就不用聽了，看看他支持小英。         0   
6359  neoa01                                現在的小英民進黨把台灣害成什麼樣子，治         1   
6361  neoa01  安交通爛、檢警調司法崩盤、88行館、人口/販運EE園區遍佈、平均3點多天就有槍擊、/少子化、...         1   
6364  neoa01                                               有夠多。         0   
6371  neoa01                                黃國昌還在那邊過去國民黨，笑死，是多不         1   
6374  neoa01                                               想醒來？         0   
7028  neoa01                       我是不會相信黃國昌的推薦啦，看看小英把/台灣搞成什麼樣子         1   
7477  neoa01                                好慘，依照國昌之前挺小英的紀錄+法律人         1   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
130              -1           0                 1  
133              -1           0                -1  
2028             -1         1.0                -1  
2386              1        -1.0                 1  
2388             -1        -1.0                 1  
2544             -1         1.0                -1  
2661             -1           0                -1  
2663             -1           0                -1  
3083             -1           0                -1  
3085             -1           0                -1  
3920             -1        -1.0                -1  
4031             -1           0                -1  
4297             -1        -1.0                -1  
4515             -1         1.0                -1  
5414             -1           0                -1  
5420             -1           0                -1  
5430             -1        -1.0                 1  
5482             -1         1.0                -1  
5499             -1         1.0                -1  
5501             -1           0                -1  
5522             -1           0                -1  
5947             -1           0                -1  
5949             -1           0                -1  
6355              1           0                -1  
6359             -1           0                -1  
6361             -1           0                -1  
6364             -1        -1.0                -1  
6371             -1           0                -1  
6374             -1           0  

In [92]:
# 記錄每個用戶的情緒次數
emotion_counts = final_with_TC2.groupby(['userid', 'RF_emotions']).size().unstack(fill_value=0)

# 計算每個用戶的emotion總次數和1, -1的使用比率
emotion_counts['total'] = emotion_counts.sum(axis=1)
emotion_counts['ratio_1'] = emotion_counts[1] / emotion_counts['total']
emotion_counts['ratio_minus_1'] = emotion_counts[-1] / emotion_counts['total']

# 設定次數門檻
threshold = 10

# 找到emotion為1和-1次數最多的前三名用戶
emotion_top_users_1 = emotion_counts[1].nlargest(3)
emotion_top_users_minus_1 = emotion_counts[-1].nlargest(3)

# 找到emotion為1和-1使用比率最高且次數大於門檻的前三名用戶
emotion_top_ratio_users_1 = emotion_counts[emotion_counts[1] > threshold]['ratio_1'].nlargest(3)
emotion_top_ratio_users_minus_1 = emotion_counts[emotion_counts[-1] > threshold]['ratio_minus_1'].nlargest(3)

# 使用模型
print("使用Random Forest得到的結果: \n")

# 輸出結果
print("emotion為1次數最多的前三名用戶:")
for user, count in emotion_top_users_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts.loc[user, 'ratio_1']:.2f}")

print("\nemotion為-1次數最多的前三名用戶:")
for user, count in emotion_top_users_minus_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts.loc[user, 'ratio_minus_1']:.2f}")

print("\nemotion為1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts.loc[user, 1.0]}")

print("\nemotion為-1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_minus_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts.loc[user, -1.0]}")

使用Random Forest得到的結果: 

emotion為1次數最多的前三名用戶:
stvn2567: 次數=11, 比例=0.28
akirakid: 次數=8, 比例=0.19
neoa01: 次數=7, 比例=0.23

emotion為-1次數最多的前三名用戶:
akirakid: 次數=15, 比例=0.35
coffee112: 次數=14, 比例=0.39
lmf770410: 次數=14, 比例=0.37

emotion為1使用比率最高且次數大於門檻的前三名用戶:
stvn2567: 比例=0.28, 次數=11

emotion為-1使用比率最高且次數大於門檻的前三名用戶:
coffee112: 比例=0.39, 次數=14
lmf770410: 比例=0.37, 次數=14
akirakid: 比例=0.35, 次數=15


In [123]:
emotion_counts = final_with_TC2.groupby(['userid', 'RF_emotions']).size().unstack(fill_value=0)

# 計算每個用戶的emotion總次數和1, -1的使用比率
emotion_counts['total'] = emotion_counts.sum(axis=1)
emotion_counts['ratio_1'] = emotion_counts[1] / emotion_counts['total']
emotion_counts['ratio_minus_1'] = emotion_counts[-1] / emotion_counts['total']
row_sums = emotion_counts.sum(axis=0)
row_sums

RF_emotions
-1.0             2351.000000
0                5358.000000
1.0              1032.000000
0                  95.000000
total            8836.000000
ratio_1           477.247872
ratio_minus_1    1060.868929
dtype: float64

In [118]:
emotion_user = useridSearch('stvn2567',final_with_all)
emotion_user

userid                                    message_content  push_tag  \
1946  stvn2567                        選前向來站綠的戰神怎麼看民進黨在桃園/和新竹的選戰打法         1   
3580  stvn2567                      支持蘇貞昌的影帝又來演了/記得拿出大打錯誤顏色的一半力道阿         1   
3653  stvn2567                                                            1   
3656  stvn2567                                            民主的大前輩們         1   
3737  stvn2567  ✓ 黃國昌在臉書發文表示，拍桌、叫囂/、潑水、打架，國民黨用這麼廉價的方式/，只是幫民進黨創...         1   
3812  stvn2567                 黃對正確的顏色不敢真的撕破臉才鬥才只/更正 只鬥抓小咖啦/只抓小咖鬥         1   
4371  stvn2567                                 今天綠營網路部都刷北北基桃要大勝利了         0   
4881  stvn2567                                        看看中崙案...不說了        -1   
7458  stvn2567                                  戰神挺蘇蔡的鐵則才是元兇 直到現在         0   
7511  stvn2567                                 他在放水一例不鬧僵、全票支持前瞻還有         0   
7513  stvn2567                                    2018撐電火球已經大賣人情了         1   
7528  stvn2567                              他在疫情期間更是安靜一兩年不嘴阿鐘的/缺失         1   
7579  stvn2567              ✓ 黃國昌在臉書發文表示，拍桌、叫囂/、潑水、打架，國民黨用這麼廉價的方式         1   
7582  stvn2567                                 ，只是幫民進黨創造極佳的藉口，質疑這         1   
7588  stvn2567                                 是認真在監督，還是根本在作球？爛透了         1   
7590  stvn2567                               ，令人失望透頂 => 時力猛批前瞻卻投贊         1   
7593  stvn2567                         成  / 前瞻條例三讀 時力：勿重蹈過去/政府的錯誤         1   
7595  stvn2567                                ✓ 時力公開表態 黃國昌：我這票投給蘇         1   
7598  stvn2567                               貞昌 / 蘇貞昌拜會時代力量 黃國昌：新         1   
7602  stvn2567                                          北這張票我有投給你         1   
7637  stvn2567             重點在於黃國昌還在當立委的時候就跪好/跪滿了 為了禮讓就大幅低頭叫新政治 好         1   
7639  stvn2567                                 意思在新北押注大敗後丟掉主席的隔年做         0   
7642  stvn2567                                         賊喊抓賊說抓小綠呵呵         1   
7664  stvn2567              爆在哪 放走陳偉智和放任雄檢辯護被告/只是吹牛嗎？根本沒有用出和北檢聯手打         0   
7666  stvn2567                                     剛好是他不喜好顏色力道的一半         0   
7696  stvn2567                                 等到他罕見指摘蘇院長的態度都客氣過頭         0   
7699  stvn2567                                  對比分水嶺之前還以為被盜號呢（有走        -1   
7702  stvn2567                                 過體制內又回到體制外裝忙不再像社運時         0   
7704  stvn2567                                           期堵人真是不一樣         0   
7716  stvn2567                   黃和時力一樣小綠不用幫忙洗了啦 舔綠/歷史的報導都變成白紙黑字了         1   
7742  stvn2567           從前KP算是2010年初的後扁系龍頭 而黃/一直是親英系社運派的領頭羊 兩人合在         1   
7745  stvn2567                                 一起要畫清權力界線又會是民進黨派系的         1   
7748  stvn2567                                 縮影了（題外話：明眼人都知道解散派系         1   
7750  stvn2567                                                是假）         0   
7789  stvn2567              黃國昌是自己押注蘇搞爛的 他負責的新/北議員選區全掛 怪誰？隔年給他鬥掉反         1   
7791  stvn2567                        綠的顯智推卸責任 換上他屬意足夠親綠/的徐還不夠爽嗎？         1   
8366  stvn2567                                       把李鴻鈞調回來比較有可能         1   
8720  stvn2567                                        戰神連陳時中都不敢嘴了         0   
8767  stvn2567                                   2018支持電火球 真的有夠良心         0   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
1946              1           0                 1  
3580             -1        -1.0                 1  
3653              1           0                -1  
3656              1           0                -1  
3737              1        -1.0                -1  
3812             -1         1.0                -1  
4371             -1           0                 1  
4881             -1           0                -1  
7458             -1           0                 1  
7511             -1           0                -1  
7513              1         1.0                -1  
7528             -1         1.0                -1  
7579              1        -1.0                 1  
7582              1         1.0                -1  
7588             -1         1.0                -1  
7590           

In [119]:
#coffee112
emotion_user = useridSearch('coffee112',final_with_all)
emotion_user

userid                           message_content  push_tag  \
743   coffee112                        黃國昌這個北爛就是推手還敢講 =_=         0   
765   coffee112     國昌是不是忘記反紅媒讓民進党一党毒大/你還支持謊紅小英呢 ~_~ 在裝無辜         1   
822   coffee112                        算了吧 九分打k 一分打民進党裝一下         0   
830   coffee112                          國昌老師會忘記的東西 真多...         1   
1118  coffee112                                                   1   
1124  coffee112                                      楊伊湄：         0   
1671  coffee112                          塑膠烏龜吧 都躲到不知道哪裡去了         1   
1880  coffee112  感謝最愛台灣抗中保台 支持民進党 呵/呵 國昌 別忘記 這就是你支持的垃圾dpp         0   
1882  coffee112                國昌你支持的謊紅小英 只會說著她什麼/都不知道 呵呵         1   
1896  coffee112                           國昌是不是忘記自己也是推手啊？         0   
2607  coffee112                         好了辣 打別人九分打民進党一分還演         0   
2609  coffee112                          垃圾無恥民進党就是你支持你的選擇         0   
2613  coffee112                          現在跟館長一樣裝做沒事人 假中壢        -1   
2615  coffee112                          謊紅小英這麼爛都忘記是誰力挺的吼         0   
2670  coffee112                           好了辣 還不是只會支持謊紅小英         0   
2970  coffee112                       黃國昌這個綠共推手還有臉出來喔？=_=         0   
2977  coffee112                         跟館長兩個北爛反紅媒 反到變一言堂         0   
2979  coffee112                         兩個都還支持謊紅小英現在都在裝無辜         0   
2996  coffee112                        去又怎樣 到最後還不是只會支持dpp        -1   
3001  coffee112                          喔 啊不就好棒棒 綠共推手裝無辜        -1   
3011  coffee112                     一個廢物kmt另一個垃圾dpp 挺了垃圾裝         0   
3013  coffee112      無辜 難道我的錯?反紅媒玩到他爆如興/案電視新聞媒體也不太報 是在搞笑膩         1   
3051  coffee112      笑死 反紅媒造就現在會自綠的新聞媒體/跟我說沒毛病真是有夠天才超適合對岸         1   
3076  coffee112                      笑死人天才 國昌817挺蔡英文 不然黃國         1   
3078  coffee112                          昌是藍的？講話之前要不要重想一次         0   
3086  coffee112                         順便跟你說 你好像非常快就被檢舉了         0   
3091  coffee112        上次這板也有人貼轉黃國昌講如興弊案/也是火速光速就被人檢舉刪除文章了         0   
3100  coffee112                        那篇如興爆文也是沒多久就消失了...         0   
3104  coffee112                         那篇如興弊案爆文 很快就被檢舉刪掉         0   
3106  coffee112                        啊不就很失望 然後選前又再歸隊dpp         0   
3162  coffee112        爆弊案再多 選前還不是歸隊說我支持民/進党 啊這樣是在搞笑膩？=_=         1   
3165  coffee112                          有沒有想過綠共怪獸的推手們是誰？         0   
3170  coffee112                        一党毒大 爆那些弊案什麼的 有下文？        -1   
3873  coffee112                                    東堂勇哥表示        -1   
7100  coffee112                                        好窩         0   
7584  coffee112                     好奇 其實這麼晚 喊加加 有意義嗎？=_=         0   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
743               1           0                -1  
765              -1        -1.0                -1  
822               1           0                 1  
830               1        -1.0                -1  
1118              1           0                -1  
1124              1           0                -1  
1671             -1        -1.0                -1  
1880             -1         1.0                 1  
1882             -1         1.0                -1  
1896              1        -1.0                -1  
2607              1           0                 1  
2609             -1        -1.0                -1  
2613             -1           0                -1  
2615              1        -1.0                 1  
2670             -1        -1.0                -1  
2970              1           0                 1  
2977              1           0                -1  
2979              1           0                -1  
2996              1        -1.0                -1  
3001              1           0                 1  
3011             -1        -1.0                -1  
3013             -1           0                -1  
3051             -1         1.0                -1  
3076              1         1.0                -1  
3078             -1        -1.0                -1  
3086             -1          

In [93]:
# 記錄每個用戶的情緒次數
emotion_counts = final_with_PC1.groupby(['userid', 'Bi-LSTM_emotions']).size().unstack(fill_value=0)

# 計算每個用戶的emotion總次數和1, -1的使用比率
emotion_counts['total'] = emotion_counts.sum(axis=1)
emotion_counts['ratio_1'] = emotion_counts[1] / emotion_counts['total']
emotion_counts['ratio_minus_1'] = emotion_counts[-1] / emotion_counts['total']

# 設定次數門檻
threshold = 10

# 找到emotion為1和-1次數最多的前三名用戶
emotion_top_users_1 = emotion_counts[1].nlargest(3)
emotion_top_users_minus_1 = emotion_counts[-1].nlargest(3)

# 找到emotion為1和-1使用比率最高且次數大於門檻的前三名用戶
emotion_top_ratio_users_1 = emotion_counts[emotion_counts[1] > threshold]['ratio_1'].nlargest(3)
emotion_top_ratio_users_minus_1 = emotion_counts[emotion_counts[-1] > threshold]['ratio_minus_1'].nlargest(3)

print("使用Bi-LSTM得到的結果: \n")

# 輸出結果
print("emotion為1次數最多的前三名用戶:")
for user, count in emotion_top_users_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts.loc[user, 'ratio_1']:.2f}")

print("\nemotion為-1次數最多的前三名用戶:")
for user, count in emotion_top_users_minus_1.items():
    print(f"{user}: 次數={count}, 比例={emotion_counts.loc[user, 'ratio_minus_1']:.2f}")

print("\nemotion為1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts.loc[user, 1.0]}")

print("\nemotion為-1使用比率最高且次數大於門檻的前三名用戶:")
for user, ratio in emotion_top_ratio_users_minus_1.items():
    print(f"{user}: 比例={ratio:.2f}, 次數={emotion_counts.loc[user, -1.0]}")

使用Bi-LSTM得到的結果: 

emotion為1次數最多的前三名用戶:
stvn2567: 次數=14, 比例=0.36
akirakid: 次數=12, 比例=0.28
coffee112: 次數=11, 比例=0.31

emotion為-1次數最多的前三名用戶:
akirakid: 次數=31, 比例=0.72
bybe: 次數=29, 比例=0.88
lmf770410: 次數=29, 比例=0.76

emotion為1使用比率最高且次數大於門檻的前三名用戶:
sellgd: 比例=0.38, 次數=11
stvn2567: 比例=0.36, 次數=14
coffee112: 比例=0.31, 次數=11

emotion為-1使用比率最高且次數大於門檻的前三名用戶:
CindyLara: 比例=1.00, 次數=11
GW1014: 比例=1.00, 次數=11
prkfcpr: 比例=1.00, 次數=14


In [124]:
# 記錄每個用戶的情緒次數
emotion_counts = final_with_PC1.groupby(['userid', 'Bi-LSTM_emotions']).size().unstack(fill_value=0)

# 計算每個用戶的emotion總次數和1, -1的使用比率
emotion_counts['total'] = emotion_counts.sum(axis=1)
emotion_counts['ratio_1'] = emotion_counts[1] / emotion_counts['total']
emotion_counts['ratio_minus_1'] = emotion_counts[-1] / emotion_counts['total']
row_sums = emotion_counts.sum(axis=0)
row_sums

Bi-LSTM_emotions
-1               7080.000000
1                1756.000000
total            8836.000000
ratio_1           775.973555
ratio_minus_1    3337.026445
dtype: float64

In [120]:
emotion_user = useridSearch('sellgd',final_with_all)
emotion_user

userid                   message_content  push_tag  LSTM_emotions  \
2389  sellgd              明明就小綠 選舉裝中立 還有TPP可選啊         0             -1   
2443  sellgd                   明明就小綠 裝中立來分非綠的票         0             -1   
6279  sellgd                 小綠又出來讓綠當選了 支持北竹雙安         1             -1   
6284  sellgd                 明明都在關鍵時幫綠 選前才在裝中立         1             -1   
6737  sellgd                 小綠又出來讓綠當選了 支持北竹雙安         0             -1   
6878  sellgd                   明明就是小綠 都幫綠多少次了?         0             -1   
6944  sellgd             綠色翟本喬 國昌 台視幫黃轉播 要分藍票?         0              1   
7083  sellgd                 小綠又出來讓綠當選了 支持北竹雙安         0             -1   
7111  sellgd                   明明就是小綠 都幫綠多少次了?         1             -1   
7121  sellgd                         高雄ID說的投33        -1             -1   
7135  sellgd                 小綠又出來讓綠當選了 支持北竹雙安         1             -1   
7143  sellgd                新北台中也是kmt，難道要投dpp?         1             -1   
7165  sellgd                   明明就是小綠 都幫綠多少次了?         0             -1   
7222  sellgd  綠色翟本喬 國昌 台視幫黃轉播 要分藍票?/只支持領先的北竹雙安         1             -1   
7770  sellgd                            小綠臥底嗎?        -1             -1   
7798  sellgd                     會不會黃國昌以前就是臥底?         0             -1   
7805  sellgd                 國昌最近幾年都輕輕打綠 重重打在野         1             -1   
7813  sellgd                 那只好下架塔綠班為重 支持北竹雙安         1              1   
7852  sellgd                  明明就親綠 民眾黨用人的標準可疑         0             -1   
7857  sellgd                現在小黨就是不夠力 只支持能拉下綠的        -1              1   
7866  sellgd                  黃國昌2020為什麼支持蔡英文?         1              1   
7873  sellgd                              重新創造         0              1   
7896  sellgd                    下架塔綠班為重 支持北竹雙安         0             -1   
7993  sellgd         有腦還會在2020支持蔡英文/還是他專業是風向王?         1             -1   
8349  sellgd                 國昌最近幾年都輕輕打綠 重重打在野         0             -1   
8379  sellgd                  黃國昌2020為什麼支持蔡英文?         1              1   
8388  sellgd                 不是好東西 和爛東西 有什麼差別?         0             -1   
8414  sellgd                    硬個頭 立場標準都變了幾次了        -1             -1   
8462  sellgd                     黃國昌 我只記得他多次助綠         1             -1   

     RF_emotions  Bi-LSTM_emotions  
2389           0                 1  
2443           0                -1  
6279           0                 1  
6284           0                -1  
6737           0                 1  
6878           0                -1  
6944           0                -1  
7083           0                 1  
7111           0                -1  
7121           0                -1  
7135           0                 1  
7143           0                 1  
7165           0                -1  
7222         1.0                -1  
7770           0                -1  
7798           0                -1  
7805           0                -1  
7813           0                 1  
7852        -1.0                -1  
7857        -1.0                -1  
7866           0                 1  
7873         1.0                -1  
7896           0                -1  
7993           0                 1  
8349           0                -1  
8379           0                 1  
8388        -1.0                -1  
8414           0                -1  
8462           0                 1

In [121]:
emotion_user = useridSearch('CindyLara',final_with_all)
emotion_user

userid                                    message_content  push_tag  \
177   CindyLara                           不挺33的話  大綠 說謊中 怎麼有機會當/選？         1   
953   CindyLara                                       還在演 到時還不是投大綠         0   
1814  CindyLara                                    講的 黃國濕 不是 小綠 一樣         0   
2247  CindyLara           真正的原因 是 想讓 33 搶一些 蔣的票/讓 說謊中 有機會當選 小綠不用裝了         1   
2532  CindyLara                                          小綠 回去躺好嗎？         0   
2844  CindyLara  小綠就是小綠 大陸月月鳥 的 中國台灣/怎麼沒看到 黃國濕 吭聲？/不挺 33 的話 說謊中...         1   
3492  CindyLara                              小綠 怎麼裝都沒用的 真正立場早就露餡/了         1   
4752  CindyLara                       expertsaid 去看看 慶富案 就知道黃是/哪種人         1   
6942  CindyLara  小綠就是小綠 根本就是幫忙分票 讓 說/謊中 當選的/之前打弊案 都是 虎頭蛇尾 完全幫到弊/案者         1   
7841  CindyLara                                      笑死 是多怕 說謊中 落選         1   
8690  CindyLara                                       小綠 早點 消失 好嗎？         0   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
177               1        -1.0                -1  
953              -1        -1.0                -1  
1814             -1        -1.0                -1  
2247              1        -1.0                -1  
2532              1           0                -1  
2844              1        -1.0                -1  
3492             -1        -1.0                -1  
4752             -1        -1.0                -1  
6942             -1           0                -1  
7841             -1        -1.0                -1  
8690              1        -1.0                -1

In [125]:
emotion_user = useridSearch('akirakid', final_with_all)
emotion_user

userid                                    message_content  push_tag  \
1732  akirakid                      靠北，我還想說美女醫誰啊點進來/直接寫基進的誰我就會無視了         1   
1854  akirakid                      時力要支持哪個候選人，不是黃國昌說了/就能代表時力支持吧。         1   
2390  akirakid                                         羨慕！我們新北...         0   
2397  akirakid                                  所以藍綠取得權力之後往哪邊倒了呢？         0   
2403  akirakid                          不然呢？當一席立委當一席議員藍綠的多/數誰鳥你呢？         1   
2418  akirakid        黃國昌他指的是基隆選區吧，他踢爆的國/家賤賣土地給黑道藍綠市長候選人都有去/黑道生日宴         1   
2423  akirakid                                       退黨的祝福啊，不然怎麼辦         0   
2428  akirakid                                 時代力量基隆有推其它議員候選人，3個         0   
2431  akirakid  如果他做不好，那沒了也沒什麼可惜，如/果他做的好，那其實跟黃國昌一樣，黃國/昌說他一個人在國...         1   
2433  akirakid  貧窮的小黨拿出錢和資源來選市長不是容/易的事，也許是錯，但是我覺得他做的好/或不好，應該比那...         1   
2436  akirakid  如果覺得別人別黨藍綠好的，就去投自己/喜歡的就好，如果覺得他做的好就投他給/他一個機會就好了...         1   
2438  akirakid                                 支持藻礁到最後的，多的是初期喊支持之         1   
2441  akirakid                                           後閉嘴的，他不是         1   
2445  akirakid              選後當側翼的話我幹嘛還看到一堆人貼鏡/電視調閱小組投票時陳椒華主席跟國民黨         1   
2447  akirakid                                               投支持票         1   
2451  akirakid                     如果沒有增加夥伴，連黨團都沒有，也沒/辦法提案，只能努力掙脫         1   
2455  akirakid                    https://i.imgur.com/oL4NAij.jpg         1   
2457  akirakid  我覺得沒有他做的好不好，只有小綠和選/市長錯誤，是因為覺得他威脅藍綠的選票/，那我會認為他只...         1   
2460  akirakid  我覺得是給一個藍綠之外的選擇，和突破/困境的努力，繼續現狀最好不過就是像黃/國昌說的一個人在...         1   
2463  akirakid                                     我覺得那就是一堆爛蘋果的例子         1   
2466  akirakid         所以我比較覺得是威脅到別黨的票，少數/小黨在國會議會面對大黨或地方勢力，我/想不好過         1   
2469  akirakid                            主張打倒炒房仔的政黨？零號候選人好像/沒有政黨         1   
2471  akirakid                    https://i.imgur.com/mXDzNCf.jpg         0   
2473  akirakid  Ours的洛書剛寫完書，名叫無住之島，吹/哨揭弊者保護協會就黃國昌辦的，公民幫/推我就不曉得...         1   
2477  akirakid                               Ours跟黃國昌一直有合作推囤房稅，到椒         0   
2479  akirakid                                    華主席年代我記得還有在推相關的         0   
2483  akirakid                                            基隆有白能選？         1   
2487  akirakid                  所以對那些退黨的我都真心感謝帶祝福/能離開時力去抗中保台真是太好了         1   
2489  akirakid           我自己認為時力黨中央對陳椒華主席的認/同和支持態度是有在維護時力自己路線的/力量         1   
2491  akirakid              苗栗兩個無黨籍的直接跑去當徐定禎發言/人，一個回頭攻擊宋國鼎，我覺得還在時         1   
2493  akirakid  力黨裡的多少還是會有一些受黨羈縻的態/度，一開始的那兩個不分區我覺得或許創/黨時期的時力就是...         1   
2500  akirakid                 基隆有民眾黨選市長？沒有的話是在講什/麼？/還是爛蘋果裝白蘋果來噓？         1   
2506  akirakid  時代力量洗過一輪之後，你看現在競選總/部成立黃國昌會到的，會去吹哨者協會辦/的活動的，就知道...         1   
2508  akirakid                          比起來我比較羨慕能對自己投的候選人那/麼有信心的人         1   
2514  akirakid                                 投票又不是買彩券，會中的才要買 XD         1   
2515  akirakid  如果覺得他不夠好，那選不上也不是什麼/問題，如果比較好，那就買一個機會/畢竟不好的選上還是從...         1   
2554  akirakid                                        你的白色側翼標準很低呢         0   
2932  akirakid                                                 高调         0   
3300  akirakid                                                 高調         0   
3720  akirakid                                                 高調         0   
4432  akirakid                                                 高調         1   
5413  akirakid                                                 高調         0   
8806  akirakid                                                 高調         0   

      LSTM_emotions RF_emotions  Bi-LSTM_emotions  
1732              1        -1.0                -1  
1854              1        -1.0                -1  
2390              1         1.0                -1  
2397              1           0                -1  
2403             -1           0                -1  
2418              1        -1.0                -1  
2423              1           0                -1  
2428              1           0                 1  
2431              1        -1.0                 1  
2433       

# 資料分析

### 黃國昌的:
8836則留言

## Push tag:
push_tag為1次數最多的前三名用戶:
akirakid: 次數=30, 比例=0.70
stvn2567: 次數=25, 比例=0.64
lmf770410: 次數=21, 比例=0.55

push_tag為-1次數最多的前三名用戶:
JT0624: 次數=6, 比例=0.46
bybe: 次數=6, 比例=0.18
coffee112: 次數=5, 比例=0.14

push_tag為1使用比率最高且次數大於門檻的前三名用戶:
porfavor: 比例=0.85, 次數=11
turbomons: 比例=0.71, 次數=12
akirakid: 比例=0.70, 次數=30

push_tag為-1使用比率最高且次數大於門檻的前三名用戶:
無(沒有超過門檻的留言數)

## Emotion:
emotion為1次數最多的前三名用戶:
akirakid: 次數=21, 比例=0.49
Newtype: 次數=19, 比例=0.54
sellgd: 次數=15, 比例=0.52

emotion為-1次數最多的前三名用戶:
stvn2567: 次數=29, 比例=0.74
bybe: 次數=28, 比例=0.85
lmf770410: 次數=24, 比例=0.63

emotion為1使用比率最高且次數大於門檻的前三名用戶:
thebestone: 比例=0.81, 次數=13
tsungmou: 比例=0.79, 次數=11
August2006: 比例=0.63, 次數=12

emotion為-1使用比率最高且次數大於門檻的前三名用戶:
widec: 比例=0.95, 次數=19
faust666: 比例=0.93, 次數=13
MicroB: 比例=0.87, 次數=20


### 柯文哲的:
留言次數最多的三名用戶：{'Tiphareth': 471, 'spzper': 403, 'MicroB': 262}

push_tag為1次數最多的前三名用戶:
Tiphareth: 次數=263, 比例=0.56
spzper: 次數=191, 比例=0.47
trywish: 次數=180, 比例=0.73

push_tag為-1次數最多的前三名用戶:
Tiphareth: 次數=68, 比例=0.14
spzper: 次數=64, 比例=0.16
freehouse: 次數=38, 比例=0.40

push_tag為1使用比率最高且次數大於門檻的前三名用戶:
Samurai: 比例=1.00, 次數=14
laughhao: 比例=1.00, 次數=28
njxmzxc: 比例=0.98, 次數=57

push_tag為-1使用比率最高且次數大於門檻的前三名用戶:
mimicat12: 比例=0.65, 次數=11
charsa: 比例=0.50, 次數=20
lemon81824: 比例=0.50, 次數=11

### Total articles
Keyword: 陳其邁
total articles  135

Keyword: 蘇貞昌
total articles  266

Keyword: 柯文哲
total articles  904

Keyword: 侯友宜
total articles  176

Keyword: 黃國昌
total articles  56